In [1]:
%load_ext rpy2.ipython

In [2]:
%%R
set.seed(88888888) # maximum luck

library(DESeq2)
library(plotly)
library(ggplot2)
library(viridis)
library(magrittr)
library(pheatmap)
library(DescTools)
library(pdfCluster)
library(RColorBrewer)
library(SummarizedExperiment)
library(caret)
library(class)
library(htmlwidgets)

Loading required package: S4Vectors
Loading required package: stats4
Loading required package: BiocGenerics

Attaching package: ‘BiocGenerics’

The following objects are masked from ‘package:stats’:

    IQR, mad, sd, var, xtabs

The following objects are masked from ‘package:base’:

    anyDuplicated, aperm, append, as.data.frame, basename, cbind,
    colnames, dirname, do.call, duplicated, eval, evalq, Filter, Find,
    get, grep, grepl, intersect, is.unsorted, lapply, Map, mapply,
    match, mget, order, paste, pmax, pmax.int, pmin, pmin.int,
    Position, rank, rbind, Reduce, rownames, sapply, setdiff, sort,
    table, tapply, union, unique, unsplit, which.max, which.min


Attaching package: ‘S4Vectors’

The following object is masked from ‘package:utils’:

    findMatches

The following objects are masked from ‘package:base’:

    expand.grid, I, unname

Loading required package: IRanges
Loading required package: GenomicRanges
Loading required package: GenomeInfoDb
Loading require

In [3]:
%%R
OUT_DIR <- "/mnt/home/yuankeji/RanceLab/reticula_new/reticula/data/tcdd/output/"
N_FOLDS <- 10

In [4]:
%%R
vst.counts <- readRDS(paste(OUT_DIR, "vst_counts.Rds", sep = ""))
print(vst.counts)

class: DESeqTransform 
dim: 4634 383 
metadata(1): version
assays(1): ''
rownames(4634): ENSMUSG00000000568 ENSMUSG00000000579 ...
  ENSMUSG00000118462 ENSMUSG00000118541
rowData names(4): baseMean baseVar allZero dispFit
colnames(383): SRR7817611 SRR7817612 ... SRR4317659 SRR4317660
colData names(3): Sample Tissue sizeFactor


In [5]:
%%R
sample <- colData(vst.counts)
print(sample)

DataFrame with 383 rows and 3 columns
                Sample    Tissue sizeFactor
           <character> <numeric>  <numeric>
SRR7817611  SRR7817611         0    1.02662
SRR7817612  SRR7817612         0    1.04842
SRR7817614  SRR7817614         0    1.37644
SRR7817615  SRR7817615         0    1.03818
SRR7817616  SRR7817616         0    1.03785
...                ...       ...        ...
SRR4317656  SRR4317656        30    2.62019
SRR4317657  SRR4317657        30    1.41057
SRR4317658  SRR4317658        30    1.37227
SRR4317659  SRR4317659        30    1.98201
SRR4317660  SRR4317660        30    1.99322


In [6]:
%%R
vst.count.mtx <-
   vst.counts %>% SummarizedExperiment::assay() %>% as.data.frame()
print(length(vst.count.mtx))
print(vst.count.mtx)

[1] 383
                   SRR7817611 SRR7817612 SRR7817614 SRR7817615 SRR7817616
ENSMUSG00000000568   19.89468   19.78997   20.06086   19.95841   20.04601
ENSMUSG00000000579   14.61781   14.33031   13.94108   14.68931   14.69199
ENSMUSG00000000581   19.94625   19.81636   20.47749   20.14210   19.99506
ENSMUSG00000000594   21.83221   21.84224   22.10274   21.38252   21.38118
ENSMUSG00000000605   20.74409   20.59634   20.98925   20.92454   20.89263
ENSMUSG00000000617   13.27759   13.27740   13.27512   13.27749   13.27749
ENSMUSG00000000627   14.15261   13.73399   13.27512   13.27749   13.27749
ENSMUSG00000000628   15.44773   15.14633   14.33818   15.06463   15.24083
ENSMUSG00000000673   24.55927   24.56579   24.78833   24.55693   24.56123
ENSMUSG00000000682   16.20645   16.44576   15.95735   15.95630   15.85783
ENSMUSG00000000693   16.86627   16.63537   16.77325   16.86020   17.01999
ENSMUSG00000000706   13.27759   13.27740   13.27512   13.27749   13.27749
ENSMUSG00000000708   20.66120 

ENSMUSG00000001964   17.84905   17.91074   18.38487   18.10191   18.11975
ENSMUSG00000001983   18.69588   18.52065   18.39797   18.75286   18.68914
ENSMUSG00000001985   13.27759   13.27740   13.27512   13.73596   13.27749
ENSMUSG00000001986   14.75954   15.17436   13.82776   14.55149   14.47753
ENSMUSG00000001998   16.90794   16.52293   16.82844   16.90043   16.71495
ENSMUSG00000001999   17.51444   17.31027   17.52006   17.12726   17.31699
ENSMUSG00000002010   21.19274   21.18099   21.07700   21.43019   21.41839
ENSMUSG00000002015   21.91197   21.93317   22.29460   21.89818   21.90990
ENSMUSG00000002020   14.97159   15.22056   14.39876   15.45209   15.25424
ENSMUSG00000002028   19.20020   19.24224   19.37672   19.53171   19.32265
ENSMUSG00000002031   18.52428   18.56078   19.13410   18.85978   18.60698
ENSMUSG00000002033   14.59788   14.62254   14.12364   14.79425   14.80238
ENSMUSG00000002043   17.14960   17.49627   17.49595   17.06179   16.81114
ENSMUSG00000002052   20.69542   20.619

ENSMUSG00000003099   20.31271   20.40871   20.34242   20.42305   20.32416
ENSMUSG00000003119   18.11570   18.13697   18.49143   18.30233   18.24035
ENSMUSG00000003131   19.44000   19.48471   19.22749   19.29958   19.37847
ENSMUSG00000003135   18.47742   18.22564   18.71653   18.40193   18.52470
ENSMUSG00000003153   14.97562   14.48630   14.39994   14.49054   14.56132
ENSMUSG00000003161   18.98990   19.04794   19.21236   19.09875   19.03193
ENSMUSG00000003184   20.97977   20.72307   20.92577   20.90850   20.88142
ENSMUSG00000003200   18.70344   18.65560   18.70031   18.73903   18.88083
ENSMUSG00000003206   14.49854   14.42211   14.83504   14.75048   14.56132
ENSMUSG00000003360   20.48335   20.61965   20.36474   20.65304   20.86778
ENSMUSG00000003435   21.42726   21.38884   20.82677   21.21745   21.19194
ENSMUSG00000003436   13.27759   13.27740   13.27512   13.27749   13.27749
ENSMUSG00000003437   19.59776   19.39917   19.60407   19.33809   19.03449
ENSMUSG00000003444   16.04801   15.605

ENSMUSG00000001494   13.68889   13.27551   13.67059   13.27443   13.27314
ENSMUSG00000001504   13.27555   13.27551   13.27456   13.27443   13.27314
ENSMUSG00000001506   21.71311   21.70666   21.33951   21.48232   22.29267
ENSMUSG00000001507   17.83878   17.97587   17.37636   17.63278   19.77759
ENSMUSG00000001517   16.29145   15.80148   15.97001   16.00418   15.74151
ENSMUSG00000001518   17.76462   17.70694   17.46305   17.35906   17.99654
ENSMUSG00000001521   16.05937   16.12743   15.45160   15.76441   16.62220
ENSMUSG00000001524   18.09090   18.22228   17.27396   17.00117   16.90120
ENSMUSG00000001542   17.86578   18.01443   20.24822   20.10207   20.14149
ENSMUSG00000001552   19.43770   19.24434   18.85568   19.00652   19.85693
ENSMUSG00000001622   13.27555   13.27551   14.09520   13.91414   13.76674
ENSMUSG00000001632   17.43400   17.54184   17.98210   17.98965   18.47964
ENSMUSG00000001642   16.65583   16.82218   16.01848   15.75750   16.47053
ENSMUSG00000001656   13.27555   13.275

ENSMUSG00000002699   16.89668   16.65553   17.44868   17.42989   17.30317
ENSMUSG00000002731   16.72267   16.71832   17.07534   16.95317   16.68193
ENSMUSG00000002733   17.31999   17.47163   18.36383   18.53604   18.67677
ENSMUSG00000002741   19.83305   20.01772   20.31933   20.12848   20.41300
ENSMUSG00000002748   19.87455   19.95772   21.08093   21.01784   20.63284
ENSMUSG00000002763   22.91324   22.85511   21.87391   21.82778   21.58466
ENSMUSG00000002767   21.13837   21.11538   18.95770   19.10290   18.79993
ENSMUSG00000002769   24.18902   24.21455   22.94514   22.91803   21.80053
ENSMUSG00000002771   14.36586   13.95629   13.91927   14.00658   14.19041
ENSMUSG00000002778   22.09736   22.02212   21.12661   21.04449   21.10218
ENSMUSG00000002797   17.19195   17.00538   16.70224   16.99308   15.86541
ENSMUSG00000002799   14.69358   14.47762   14.35632   14.34165   15.44674
ENSMUSG00000002803   17.88021   17.73652   16.91773   16.56645   16.28114
ENSMUSG00000002804   19.01841   19.101

...

   22.04464   22.05471   22.51221   22.49874
ENSMUSG00000003534   14.88226   14.70943   14.72006   14.67280   14.48962
ENSMUSG00000003541   14.72284   14.86567   15.18805   15.49865   15.77193
ENSMUSG00000003546   20.81489   20.61102   20.65271   20.59638   20.63009
ENSMUSG00000003549   16.14344   15.74948   15.92972   15.73076   15.79747
ENSMUSG00000003555   20.11301   18.47295   18.83793   18.75239   18.73042
ENSMUSG00000003559   20.38946   20.41663   20.49677   19.96299   20.09758
ENSMUSG00000003573   16.41656   16.69790   16.69819   16.86309   16.29605
ENSMUSG00000003604   17.51591   17.08816   17.10412   17.49465   17.53876
ENSMUSG00000003617   25.43277   25.71906   25.74153   25.42619   25.42771
ENSMUSG00000003623   24.45765   24.95809   24.95725   24.53017   24.55053
ENSMUSG00000003644   18.01804   17.98704   17.81507   18.37481   18.19023
ENSMUSG00000003660   21.24506   21.32493   21.39819   20.93639   20.93250
ENSMUSG00000003665   13.27418   13.27431   13.27431   13.67498   13

ENSMUSG00000001773   13.27726   13.27755   13.27498   13.27407   13.27883
ENSMUSG00000001786   18.02504   18.31208   18.17718   18.23487   18.40578
ENSMUSG00000001794   21.18677   21.06144   21.54586   21.27137   21.37831
ENSMUSG00000001804   13.27726   13.27755   13.27498   13.27407   13.27883
ENSMUSG00000001827   14.02647   13.90570   13.27498   13.79529   13.27883
ENSMUSG00000001833   20.52979   20.58442   20.07693   20.29200   20.01971
ENSMUSG00000001847   21.77973   21.84364   21.87327   22.04897   21.96319
ENSMUSG00000001855   18.10938   18.05653   17.93848   17.94768   18.46488
ENSMUSG00000001865   13.27726   13.27755   13.27498   13.27407   13.27883
ENSMUSG00000001870   15.67111   15.20020   15.94666   16.14286   15.13583
ENSMUSG00000001891   23.78556   23.79967   23.41390   22.87387   23.37643
ENSMUSG00000001901   13.27726   13.27755   13.27498   13.27407   13.27883
ENSMUSG00000001918   16.11553   16.14800   16.17101   18.16460   15.86996
ENSMUSG00000001924   22.61877   22.713

ENSMUSG00000002963   18.68381   18.69898   18.80725   18.84660   19.22597
ENSMUSG00000002968   19.53365   19.59658   20.02681   19.94229   19.24140
ENSMUSG00000002983   14.12030   14.90803   14.49357   15.32013   15.20097
ENSMUSG00000002984   19.10972   18.80124   19.42313   19.32722   18.68559
ENSMUSG00000002985   28.78267   28.79462   28.83651   28.25653   29.06530
ENSMUSG00000002992   22.70995   22.66677   22.69947   22.76968   22.81606
ENSMUSG00000003031   20.03433   20.01732   20.27604   20.69004   19.82696
ENSMUSG00000003032   15.55291   15.28973   14.90690   15.81423   15.02722
ENSMUSG00000003033   19.12305   18.93369   19.30731   18.82398   19.10074
ENSMUSG00000003037   21.06179   21.27490   21.15870   20.87487   20.79834
ENSMUSG00000003039   20.28668   20.03994   20.35987   20.36256   20.08017
ENSMUSG00000003051   13.73070   13.90570   13.82349   14.13175   14.31682
ENSMUSG00000003053   26.58271   26.57659   26.64240   26.35944   26.19573
ENSMUSG00000003062   16.79431   17.048

ENSMUSG00000001300   16.33842   16.06803   15.80539   15.67557   15.75340
ENSMUSG00000001313   17.76342   17.78762   17.26567   17.46490   18.11553
ENSMUSG00000001323   22.10969   22.17566   22.24951   22.19152   22.16899
ENSMUSG00000001348   21.55671   21.57808   21.73724   21.83099   21.94299
ENSMUSG00000001366   20.60710   20.64791   20.46816   20.56615   20.62101
ENSMUSG00000001383   20.30863   20.32293   20.06886   20.17029   19.96313
ENSMUSG00000001403   14.07543   13.96079   14.02188   14.11728   14.10972
ENSMUSG00000001415   19.51453   19.50724   20.16115   20.18362   19.92703
ENSMUSG00000001416   21.16448   21.15931   21.38805   21.40334   21.69453
ENSMUSG00000001419   19.50461   19.73948   20.11899   20.02125   19.56272
ENSMUSG00000001435   25.34681   25.38856   25.49141   25.46187   25.48903
ENSMUSG00000001436   18.13154   17.74330   17.70311   17.90661   17.84398
ENSMUSG00000001440   21.76615   21.77753   21.84562   21.87571   21.95485
ENSMUSG00000001441   18.86055   18.764

ENSMUSG00000002475   21.03596   21.03836   21.36675   21.32200   21.04415
ENSMUSG00000002477   17.38512   17.58760   17.09181   17.42768   17.11434
ENSMUSG00000002496   20.33159   20.36148   20.64525   20.68046   20.60728
ENSMUSG00000002500   13.77431   13.27930   14.24601   13.87372   13.27485
ENSMUSG00000002524   20.15803   20.10492   20.42873   20.47622   20.43392
ENSMUSG00000002546   19.65913   19.60800   19.97681   19.89463   19.89749
ENSMUSG00000002550   19.69853   19.71273   20.11097   20.12508   19.65322
ENSMUSG00000002588   25.46106   25.45821   25.17064   25.18202   25.28989
ENSMUSG00000002602   18.62802   18.90310   19.68177   19.70913   19.26368
ENSMUSG00000002603   15.58983   15.55523   16.11826   16.13951   16.07260
ENSMUSG00000002625   20.15133   20.11360   20.47011   20.50684   20.27598
ENSMUSG00000002633   13.27918   13.77721   13.89444   13.89407   13.93040
ENSMUSG00000002658   18.32085   18.43713   18.53049   18.48448   18.54927
ENSMUSG00000002660   19.58609   19.673

In [7]:
%%R
tcdd_dose_detail.vec <-
   readRDS(paste(OUT_DIR, "tcdd_dose_detail_vec.Rds", sep = ""))
print(tcdd_dose_detail.vec)

  [1]  0.00  0.00  0.00  0.00  0.00 30.00 30.00 30.00 30.00 30.00 30.00  0.00
 [13]  0.00  0.00  0.00  0.00  0.00 30.00 30.00 30.00 30.00 30.00 30.00  0.00
 [25]  0.00  0.00  0.00  0.00  0.00 30.00 30.00 30.00 30.00 30.00 30.00  0.00
 [37]  0.00  0.00  0.00  0.00  0.00 30.00 30.00 30.00 30.00 30.00 30.00  0.00
 [49]  0.00  0.00  0.00  0.00 30.00 30.00 30.00 30.00 30.00  0.00  0.00  0.00
 [61]  0.00  0.00  0.00 30.00 30.00 30.00 30.00 30.00 30.00  0.00  0.00  0.00
 [73]  0.00 30.00 30.00 30.00 30.00 30.00 30.00  0.00  0.00  0.00  0.00  0.00
 [85]  0.00 30.00 30.00 30.00 30.00 30.00 30.00  0.00  0.00 30.00  0.00  0.00
 [97]  0.00  0.00  0.00  0.00  0.00  0.00  0.01  0.01  0.01  0.01  0.01  0.01
[109]  0.01

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [8]:
%%R
rxn2ensembls.nls <-
   readRDS(paste(OUT_DIR, "rxn2ensembls_nls.Rds", sep = ""))
print(length(rxn2ensembls.nls))
print(rxn2ensembls.nls)

[1] 7839
$`R-MMU-450466`
 [1] "ENSMUSG00000000568" "ENSMUSG00000002102" "ENSMUSG00000018286"
 [4] "ENSMUSG00000021024" "ENSMUSG00000021178" "ENSMUSG00000021737"
 [7] "ENSMUSG00000021832" "ENSMUSG00000029440" "ENSMUSG00000030591"
[10] "ENSMUSG00000030603" "ENSMUSG00000030751" "ENSMUSG00000032869"
[13] "ENSMUSG00000040850" "ENSMUSG00000068749" "ENSMUSG00000069744"
[16] "ENSMUSG00000078652" "ENSMUSG00000079197"

$`R-MMU-450551`
[1] "ENSMUSG00000000568" "ENSMUSG00000022283" "ENSMUSG00000090877"
[4] "ENSMUSG00000091971"

$`R-MMU-450580`
[1] "ENSMUSG00000000568" "ENSMUSG00000022283" "ENSMUSG00000090877"
[4] "ENSMUSG00000091971"

$`R-MMU-72103`
 [1] "ENSMUSG00000000568" "ENSMUSG00000002658" "ENSMUSG00000006498"
 [4] "ENSMUSG00000007850" "ENSMUSG00000018379" "ENSMUSG00000019738"
 [7] "ENSMUSG00000021018" "ENSMUSG00000021546" "ENSMUSG00000024097"
[10] "ENSMUSG00000028330" "ENSMUSG00000029250" "ENSMUSG00000029538"
[13] "ENSMUSG00000030795" "ENSMUSG00000031060" "ENSMUSG00000031134"
[16] "ENSMUSG0

[16] "ENSMUSG00000023944" "ENSMUSG00000024290" "ENSMUSG00000024387"
[19] "ENSMUSG00000025261" "ENSMUSG00000025289" "ENSMUSG00000027907"
[22] "ENSMUSG00000028163" "ENSMUSG00000028452" "ENSMUSG00000029171"
[25] "ENSMUSG00000030225" "ENSMUSG00000030314" "ENSMUSG00000030447"
[28] "ENSMUSG00000030681" "ENSMUSG00000030695" "ENSMUSG00000030793"
[31] "ENSMUSG00000031626" "ENSMUSG00000031825" "ENSMUSG00000031827"
[34] "ENSMUSG00000033307" "ENSMUSG00000033400" "ENSMUSG00000034994"
[37] "ENSMUSG00000035697" "ENSMUSG00000036427" "ENSMUSG00000037351"
[40] "ENSMUSG00000039224" "ENSMUSG00000044734" "ENSMUSG00000052234"
[43] "ENSMUSG00000053436" "ENSMUSG00000060791" "ENSMUSG00000060803"
[46] "ENSMUSG00000061780" "ENSMUSG00000062867" "ENSMUSG00000068417"
[49] "ENSMUSG00000068749" "ENSMUSG00000092074" "ENSMUSG00000095677"
[52] "ENSMUSG00000096255" "ENSMUSG00000098112" "ENSMUSG00000114515"
[55] "ENSMUSG00000115338"

$`R-MMU-6800434`
 [1] "ENSMUSG00000000579" "ENSMUSG00000000787" "ENSMUSG00000001016"
 [4]

[28] "ENSMUSG00000031861" "ENSMUSG00000031980" "ENSMUSG00000034117"
[31] "ENSMUSG00000034855" "ENSMUSG00000035042" "ENSMUSG00000036353"
[34] "ENSMUSG00000036362" "ENSMUSG00000036381" "ENSMUSG00000036402"
[37] "ENSMUSG00000036437" "ENSMUSG00000037346" "ENSMUSG00000039809"
[40] "ENSMUSG00000039904" "ENSMUSG00000040016" "ENSMUSG00000040495"
[43] "ENSMUSG00000040552" "ENSMUSG00000040899" "ENSMUSG00000043895"
[46] "ENSMUSG00000044014" "ENSMUSG00000044034" "ENSMUSG00000044052"
[49] "ENSMUSG00000044199" "ENSMUSG00000044288" "ENSMUSG00000044337"
[52] "ENSMUSG00000044338" "ENSMUSG00000044359" "ENSMUSG00000051980"
[55] "ENSMUSG00000052229" "ENSMUSG00000052270" "ENSMUSG00000052336"
[58] "ENSMUSG00000052850" "ENSMUSG00000058250" "ENSMUSG00000060701"
[61] "ENSMUSG00000060735" "ENSMUSG00000061353" "ENSMUSG00000062585"
[64] "ENSMUSG00000063239" "ENSMUSG00000063594" "ENSMUSG00000068523"
[67] "ENSMUSG00000071005" "ENSMUSG00000071658" "ENSMUSG00000074715"
[70] "ENSMUSG00000079227" "ENSMUSG00000094686" "

[28] "ENSMUSG00000069302" "ENSMUSG00000069303" "ENSMUSG00000069305"
[31] "ENSMUSG00000069306" "ENSMUSG00000069307" "ENSMUSG00000069308"
[34] "ENSMUSG00000069309" "ENSMUSG00000069310" "ENSMUSG00000074403"
[37] "ENSMUSG00000091405" "ENSMUSG00000093769" "ENSMUSG00000094248"
[40] "ENSMUSG00000094338" "ENSMUSG00000094777" "ENSMUSG00000095217"
[43] "ENSMUSG00000096010" "ENSMUSG00000099517" "ENSMUSG00000099583"
[46] "ENSMUSG00000100210" "ENSMUSG00000101355" "ENSMUSG00000101972"
[49] "ENSMUSG00000114279" "ENSMUSG00000114456"

$`R-MMU-8937016`
 [1] "ENSMUSG00000000708" "ENSMUSG00000002028" "ENSMUSG00000006307"
 [4] "ENSMUSG00000018102" "ENSMUSG00000031162" "ENSMUSG00000031575"
 [7] "ENSMUSG00000038384" "ENSMUSG00000060639" "ENSMUSG00000060678"
[10] "ENSMUSG00000060743" "ENSMUSG00000060981" "ENSMUSG00000061615"
[13] "ENSMUSG00000061991" "ENSMUSG00000062727" "ENSMUSG00000063021"
[16] "ENSMUSG00000068854" "ENSMUSG00000068855" "ENSMUSG00000069265"
[19] "ENSMUSG00000069266" "ENSMUSG00000069267" "ENS

[40] "ENSMUSG00000029999" "ENSMUSG00000030043" "ENSMUSG00000030327"
[43] "ENSMUSG00000030638" "ENSMUSG00000031098" "ENSMUSG00000032094"
[46] "ENSMUSG00000033335" "ENSMUSG00000033419" "ENSMUSG00000033855"
[49] "ENSMUSG00000035020" "ENSMUSG00000035152" "ENSMUSG00000035864"
[52] "ENSMUSG00000039361" "ENSMUSG00000039735" "ENSMUSG00000039959"
[55] "ENSMUSG00000040855" "ENSMUSG00000040990" "ENSMUSG00000047126"
[58] "ENSMUSG00000062234" "ENSMUSG00000062542" "ENSMUSG00000062825"
[61] "ENSMUSG00000068240" "ENSMUSG00000068923" "ENSMUSG00000079426"
[64] "ENSMUSG00000090137" "ENSMUSG00000100241"

$`R-MMU-8875320`
 [1] "ENSMUSG00000000711" "ENSMUSG00000001768" "ENSMUSG00000017831"
 [4] "ENSMUSG00000019173" "ENSMUSG00000021218" "ENSMUSG00000024883"
 [7] "ENSMUSG00000025340" "ENSMUSG00000044037" "ENSMUSG00000044456"
[10] "ENSMUSG00000051735"

$`R-MMU-5334134`
 [1] "ENSMUSG00000000730" "ENSMUSG00000018102" "ENSMUSG00000020661"
 [4] "ENSMUSG00000060639" "ENSMUSG00000060678" "ENSMUSG00000060743"
 [7] "E

...

[1] "ENSMUSG00000036390"

$`R-MMU-70471`
[1] "ENSMUSG00000036427"

$`R-MMU-70475`
[1] "ENSMUSG00000036427"

$`R-MMU-6781899`
[1] "ENSMUSG00000036432"

$`R-MMU-1234164`
[1] "ENSMUSG00000036450"

$`R-MMU-8938913`
[1] "ENSMUSG00000036461"

$`R-NUL-9620900`
[1] "ENSMUSG00000036478"

$`R-MMU-1679098`
[1] "ENSMUSG00000036499"

$`R-MMU-187895`
[1] "ENSMUSG00000036499"

$`R-MMU-1168635`
[1] "ENSMUSG00000036526" "ENSMUSG00000052889"

$`R-MMU-202394`
[1] "ENSMUSG00000036526"

$`R-MMU-202437`
[1] "ENSMUSG00000036526"

$`R-MMU-202443`
[1] "ENSMUSG00000036526"

$`R-MMU-2730863`
[1] "ENSMUSG00000036526"

$`R-MMU-2730902`
[1] "ENSMUSG00000036526"

$`R-MMU-6809764`
[1] "ENSMUSG00000036529"

$`R-MMU-6809777`
[1] "ENSMUSG00000036529"

$`R-MMU-6809778`
[1] "ENSMUSG00000036529"

$`R-MMU-9605682`
[1] "ENSMUSG00000036587"

$`R-MMU-5692480`
[1] "ENSMUSG00000036622"

$`R-MMU-446214`
[1] "ENSMUSG00000036632"

$`R-MMU-2730959`
[1] "ENSMUSG00000036636"

$`R-MMU-2395818`
[1] "ENSMUSG00000036639"

$`R-MMU-2395849`

[1] "ENSMUSG00000040511"

$`R-MMU-420593`
[1] "ENSMUSG00000040511"

$`R-MMU-964759`
[1] "ENSMUSG00000040520"

$`R-MMU-1678921`
[1] "ENSMUSG00000040522"

$`R-MMU-1678923`
[1] "ENSMUSG00000040522"

$`R-MMU-1678944`
[1] "ENSMUSG00000040522"

$`R-MMU-1678998`
[1] "ENSMUSG00000040522"

$`R-MMU-444647`
[1] "ENSMUSG00000040552"

$`R-MMU-9748996`
[1] "ENSMUSG00000040562" "ENSMUSG00000057933" "ENSMUSG00000111709"

$`R-MMU-427570`
[1] "ENSMUSG00000040569"

$`R-MMU-2161526`
[1] "ENSMUSG00000040584"

$`R-MMU-9659680`
[1] "ENSMUSG00000040584"

$`R-MMU-9759454`
[1] "ENSMUSG00000040584"

$`R-MMU-9759461`
[1] "ENSMUSG00000040584"

$`R-MMU-983696`
 [1] "ENSMUSG00000040592" "ENSMUSG00000093838" "ENSMUSG00000093861"
 [4] "ENSMUSG00000094029" "ENSMUSG00000094134" "ENSMUSG00000094174"
 [7] "ENSMUSG00000094194" "ENSMUSG00000094335" "ENSMUSG00000094491"
[10] "ENSMUSG00000094505" "ENSMUSG00000094951" "ENSMUSG00000095117"
[13] "ENSMUSG00000095170" "ENSMUSG00000095210" "ENSMUSG00000095285"
[16] "ENSMUSG00000095

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



$`R-MMU-5362564`
[1] "ENSMUSG00000074207"

$`R-MMU-71707`
[1] "ENSMUSG00000074207"

$`R-MMU-188979`
[1] "ENSMUSG00000074268" "ENSMUSG00000093931" "ENSMUSG00000096569"
[4] "ENSMUSG00000096770"

$`R-MMU-191114`
[1] "ENSMUSG00000074268" "ENSMUSG00000093931" "ENSMUSG00000096569"
[4] "ENSMUSG00000096770"

$`R-MMU-202717`
[1] "ENSMUSG00000074272"

$`R-MMU-964811`
[1] "ENSMUSG00000074361"

$`R-MMU-8985018`
[1] "ENSMUSG00000074483"

$`R-MMU-8985025`
[1] "ENSMUSG00000074483"

$`R-MMU-8985233`
[1] "ENSMUSG00000074483"

$`R-MMU-6807214`
[1] "ENSMUSG00000074486"

$`R-MMU-6807229`
[1] "ENSMUSG00000074486"

$`R-MMU-947514`
[1] "ENSMUSG00000074576"

$`R-MMU-176059`
[1] "ENSMUSG00000074604"

$`R-MMU-5423653`
[1] "ENSMUSG00000074604"

$`R-MMU-9832829`
[1] "ENSMUSG00000074637"

$`R-MMU-6809521`
[1] "ENSMUSG00000074665"

$`R-MMU-202703`
[1] "ENSMUSG00000074677" "ENSMUSG00000078780" "ENSMUSG00000078783"
[4] "ENSMUSG00000095028" "ENSMUSG00000095788"

$`R-MMU-391168`
[1] "ENSMUSG00000074677" "ENSMUSG0000007

 [4] "ENSMUSG00000094134" "ENSMUSG00000094174" "ENSMUSG00000094194"
 [7] "ENSMUSG00000094335" "ENSMUSG00000094491" "ENSMUSG00000094505"
[10] "ENSMUSG00000094951" "ENSMUSG00000095117" "ENSMUSG00000095170"
[13] "ENSMUSG00000095210" "ENSMUSG00000095285" "ENSMUSG00000095429"
[16] "ENSMUSG00000095497" "ENSMUSG00000095571" "ENSMUSG00000095612"
[19] "ENSMUSG00000095737" "ENSMUSG00000096336" "ENSMUSG00000096407"
[22] "ENSMUSG00000096580" "ENSMUSG00000102301" "ENSMUSG00000102364"

$`R-MMU-2454208`
 [1] "ENSMUSG00000093838" "ENSMUSG00000093861" "ENSMUSG00000094029"
 [4] "ENSMUSG00000094134" "ENSMUSG00000094174" "ENSMUSG00000094194"
 [7] "ENSMUSG00000094335" "ENSMUSG00000094491" "ENSMUSG00000094505"
[10] "ENSMUSG00000094951" "ENSMUSG00000095117" "ENSMUSG00000095170"
[13] "ENSMUSG00000095210" "ENSMUSG00000095285" "ENSMUSG00000095429"
[16] "ENSMUSG00000095497" "ENSMUSG00000095571" "ENSMUSG00000095612"
[19] "ENSMUSG00000095737" "ENSMUSG00000096336" "ENSMUSG00000096407"
[22] "ENSMUSG00000096580" "ENS

In [9]:
%%R
rxns <- rxn2ensembls.nls %>% names()
print(length(rxns))
print(rxns)

[1] 7839
   [1] "R-MMU-450466"  "R-MMU-450551"  "R-MMU-450580"  "R-MMU-72103"  
   [5] "R-MMU-9770119" "R-MMU-9770141" "R-MMU-9770142" "R-MMU-9770145"
   [9] "R-MMU-9770236" "R-MMU-6798748" "R-MMU-6800434" "R-MMU-6791218"
  [13] "R-MMU-6791222" "R-MMU-1605595" "R-MMU-1605624" "R-MMU-1605717"
  [17] "R-MMU-6798751" "R-MMU-9840795" "R-MMU-9840833" "R-MMU-9840884"
  [21] "R-MMU-2730692" "R-MMU-373075"  "R-MMU-380073"  "R-MMU-749454" 
  [25] "R-MMU-749456"  "R-MMU-9696268" "R-MMU-70420"   "R-MMU-71218"  
  [29] "R-MMU-8940388" "R-MMU-2002466" "R-MMU-2022141" "R-MMU-2129375"
  [33] "R-MMU-2395340" "R-MMU-8851044" "R-MMU-8938431" "R-MMU-1912394"
  [37] "R-MMU-2032794" "R-MMU-2065441" "R-MMU-212356"  "R-MMU-2247925"
  [41] "R-MMU-4396387" "R-MMU-5211235" "R-MMU-5250930" "R-MMU-5691381"
  [45] "R-MMU-8878220" "R-MMU-8936481" "R-MMU-8936621" "R-MMU-8937016"
  [49] "R-MMU-8937050" "R-MMU-9016782" "R-MMU-9016859" "R-MMU-9016915"
  [53] "R-MMU-9017420" "R-MMU-9023860" "R-MMU-9620515" "R-MMU-967705

 [461] "R-MMU-2213248" "R-MMU-2316350" "R-MMU-2467809" "R-MMU-2467811"
 [465] "R-MMU-2468287" "R-MMU-2484822" "R-MMU-375302"  "R-MMU-445071" 
 [469] "R-MMU-5610733" "R-MMU-5610767" "R-MMU-5618080" "R-MMU-5618328"
 [473] "R-MMU-5618331" "R-MMU-5624949" "R-MMU-5624952" "R-MMU-5625416"
 [477] "R-MMU-5625421" "R-MMU-5625424" "R-MMU-5625426" "R-MMU-5666169"
 [481] "R-MMU-5672329" "R-MMU-6809003" "R-MMU-6809006" "R-MMU-6811423"
 [485] "R-MMU-6811426" "R-MMU-8849350" "R-MMU-8849353" "R-MMU-8852280"
 [489] "R-MMU-8852298" "R-MMU-8852306" "R-MMU-8865774" "R-MMU-8867370"
 [493] "R-MMU-9610428" "R-MMU-9610641" "R-MMU-9646393" "R-MMU-9646679"
 [497] "R-MMU-9646685" "R-MMU-9648017" "R-MMU-9648114" "R-MMU-9668419"
 [501] "R-MMU-983259"  "R-MMU-983266"  "R-MMU-9836404" "R-MMU-3769397"
 [505] "R-MMU-9832124" "R-MMU-9832199" "R-MMU-114577"  "R-MMU-114600" 
 [509] "R-MMU-114670"  "R-MMU-114671"  "R-MMU-139842"  "R-MMU-1454757"
 [513] "R-MMU-1454822" "R-MMU-1474266" "R-MMU-2002428" "R-MMU-2002440"
 [517]

 [921] "R-MMU-9818954" "R-MMU-9821235" "R-MMU-9821368" "R-MMU-5617824"
 [925] "R-MMU-198955"  "R-MMU-202165"  "R-MMU-202168"  "R-MMU-202174" 
 [929] "R-MMU-202214"  "R-MMU-202216"  "R-MMU-202233"  "R-MMU-202245" 
 [933] "R-MMU-202248"  "R-MMU-202291"  "R-MMU-202307"  "R-MMU-202344" 
 [937] "R-MMU-2029268" "R-MMU-2029270" "R-MMU-2029271" "R-MMU-2029272"
 [941] "R-MMU-2029273" "R-MMU-2029452" "R-MMU-2029453" "R-MMU-2029455"
 [945] "R-MMU-2029457" "R-MMU-2029458" "R-MMU-2029459" "R-MMU-2029476"
 [949] "R-MMU-2197697" "R-MMU-389758"  "R-MMU-8850326" "R-MMU-8850356"
 [953] "R-MMU-8852200" "R-MMU-8855381" "R-MMU-8866277" "R-MMU-8867754"
 [957] "R-MMU-8867756" "R-MMU-8868071" "R-MMU-8868072" "R-MMU-8877475"
 [961] "R-MMU-112392"  "R-MMU-112395"  "R-MMU-112396"  "R-MMU-113411" 
 [965] "R-MMU-113412"  "R-MMU-113413"  "R-MMU-113414"  "R-MMU-113429" 
 [969] "R-MMU-1363303" "R-MMU-1363306" "R-MMU-1363311" "R-MMU-1363314"
 [973] "R-MMU-157906"  "R-MMU-187520"  "R-MMU-187552"  "R-MMU-187574" 
 [977]

[1381] "R-MMU-9013059" "R-MMU-9013284" "R-MMU-8952630" "R-MMU-8952631"
[1385] "R-MMU-6810464" "R-MMU-5685341" "R-MMU-5685838" "R-MMU-5685985"
[1389] "R-MMU-5685994" "R-MMU-5686398" "R-MMU-5686440" "R-MMU-5693539"
[1393] "R-MMU-5693584" "R-MMU-5693620" "R-MMU-5681987" "R-MMU-5682377"
[1397] "R-MMU-6799203" "R-MMU-8869425" "R-MMU-68919"   "R-MMU-68940"  
[1401] "R-MMU-68944"   "R-MMU-69019"   "R-MMU-9749253" "R-MMU-9757258"
[1405] "R-MMU-444773"  "R-MMU-879674"  "R-MMU-2426496" "R-MMU-2426528"
[1409] "R-MMU-2426626" "R-MMU-2447193" "R-MMU-2447196" "R-MMU-2465886"
[1413] "R-MMU-2533953" "R-MMU-443785"  "R-MMU-8878599" "R-MMU-9619682"
[1417] "R-NUL-2426616" "R-NUL-2467092" "R-NUL-2533890" "R-NUL-3907289"
[1421] "R-MMU-1236956" "R-MMU-1236958" "R-MMU-2187263" "R-MMU-2247512"
[1425] "R-MMU-434381"  "R-MMU-481044"  "R-MMU-8869667" "R-MMU-168162" 
[1429] "R-MMU-2730868" "R-MMU-450337"  "R-MMU-177479"  "R-MMU-2130486"
[1433] "R-MMU-2130640" "R-MMU-2130725" "R-MMU-392748"  "R-MMU-392749" 
[1437]

[1841] "R-MMU-8985950" "R-MMU-9012652" "R-MMU-9012653" "R-MMU-9012656"
[1845] "R-MMU-919404"  "R-MMU-921155"  "R-MMU-9645128" "R-MMU-9645133"
[1849] "R-MMU-9645136" "R-MMU-74993"   "R-MMU-9014449" "R-MMU-109700" 
[1853] "R-MMU-109702"  "R-MMU-1449591" "R-MMU-1458507" "R-MMU-5263624"
[1857] "R-MMU-189398"  "R-MMU-1564164" "R-MMU-2327695" "R-MMU-2396370"
[1861] "R-MMU-375151"  "R-MMU-382054"  "R-MMU-8944223" "R-MMU-212222" 
[1865] "R-MMU-212269"  "R-MMU-4655431" "R-MMU-5336365" "R-MMU-5336369"
[1869] "R-MMU-573336"  "R-MMU-573376"  "R-MMU-573383"  "R-MMU-210420" 
[1873] "R-MMU-265645"  "R-MMU-1605591" "R-MMU-1605632" "R-MMU-1605724"
[1877] "R-MMU-1605736" "R-MMU-1606312" "R-MMU-1606564" "R-MMU-1606602"
[1881] "R-MMU-1606807" "R-MMU-351341"  "R-MMU-5336182" "R-MMU-5336184"
[1885] "R-MMU-9840334" "R-MMU-9840470" "R-MMU-9840488" "R-MMU-9841189"
[1889] "R-MMU-9842115" "R-MMU-1168638" "R-MMU-168140"  "R-MMU-202500" 
[1893] "R-MMU-202534"  "R-MMU-202541"  "R-MMU-2730876" "R-MMU-450346" 
[1897]

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



 "R-MMU-4420153" "R-MMU-4420202"
[4473] "R-MMU-4420206" "R-MMU-5218640" "R-MMU-5218642" "R-MMU-5218645"
[4477] "R-MMU-5218806" "R-MMU-5218815" "R-MMU-5218818" "R-MMU-5218824"
[4481] "R-MMU-5218830" "R-MMU-5218836" "R-MMU-9679477" "R-MMU-9691215"
[4485] "R-MMU-5655142" "R-MMU-5655170" "R-MMU-192178"  "R-MMU-419843" 
[4489] "R-MMU-420265"  "R-MMU-9702818" "R-MMU-9702849" "R-MMU-9733292"
[4493] "R-MMU-9708525" "R-MMU-2586748" "R-MMU-210300"  "R-MMU-416725" 
[4497] "R-MMU-5696358" "R-MMU-5694071" "R-MMU-266082"  "R-MMU-3257122"
[4501] "R-MMU-9837978" "R-MMU-9838004" "R-MMU-1614524" "R-MMU-6797553"
[4505] "R-MMU-6797568" "R-MMU-1011576" "R-MMU-74247"   "R-MMU-74258"  
[4509] "R-MMU-9727347" "R-MMU-9727349" "R-MMU-9748991" "R-MMU-9668389"
[4513] "R-MMU-9668405" "R-MMU-9833635" "R-MMU-9833777" "R-MMU-9833973"
[4517] "R-MMU-9834807" "R-MMU-9835121" "R-MMU-9835189" "R-MMU-9835328"
[4521] "R-MMU-9835358" "R-MMU-9835385" "R-MMU-9835454" "R-MMU-9835944"
[4525] "R-MMU-9836159" "R-MMU-9836184" "R-MM

[4929] "R-MMU-2468040" "R-MMU-2470935" "R-MMU-2545203" "R-MMU-2545253"
[4933] "R-MMU-1482695" "R-MMU-75886"   "R-MMU-4411383" "R-MMU-5334050"
[4937] "R-MMU-212007"  "R-MMU-5362525" "R-MMU-2404134" "R-MMU-2404135"
[4941] "R-MMU-2453863" "R-MMU-2453876" "R-MMU-508040"  "R-MMU-2214330"
[4945] "R-MMU-2045911" "R-MMU-8985822" "R-MMU-8985829" "R-MMU-9010235"
[4949] "R-MMU-5226999" "R-MMU-5624130" "R-MMU-5624133" "R-MMU-5638004"
[4953] "R-MMU-5638006" "R-MMU-5638007" "R-MMU-5638016" "R-MMU-141186" 
[4957] "R-MMU-374909"  "R-MMU-379382"  "R-MMU-379395"  "R-MMU-9677917"
[4961] "R-MMU-8948139" "R-MMU-8948143" "R-MMU-8948146" "R-MMU-8959571"
[4965] "R-MMU-8959573" "R-MMU-2162066" "R-MMU-74248"   "R-MMU-9754916"
[4969] "R-MMU-9755078" "R-NUL-3221949" "R-MMU-8853745" "R-MMU-8853789"
[4973] "R-MMU-8853800" "R-MMU-8871226" "R-MMU-9830749" "R-MMU-9830756"
[4977] "R-MMU-192475"  "R-MMU-5251942" "R-MMU-5251955" "R-MMU-5251959"
[4981] "R-MMU-5252079" "R-MMU-372542"  "R-MMU-380586"  "R-MMU-444160" 
[4985]

[5389] "R-MMU-2193065" "R-MMU-2197579" "R-MMU-2976706" "R-MMU-2976707"
[5393] "R-MMU-2976723" "R-NUL-1986584" "R-NUL-2197556" "R-MMU-114683" 
[5397] "R-MMU-76590"   "R-MMU-9026777" "R-MMU-5226904" "R-MMU-6784598"
[5401] "R-MMU-1306957" "R-MMU-1306963" "R-MMU-1306965" "R-MMU-179883" 
[5405] "R-MMU-8864029" "R-MMU-9018572" "R-MMU-9018573" "R-MMU-382057" 
[5409] "R-MMU-382061"  "R-MMU-2022399" "R-MMU-9645428" "R-MMU-9645481"
[5413] "R-MMU-9645501" "R-MMU-9645520" "R-MMU-9645524" "R-MMU-9645535"
[5417] "R-MMU-416929"  "R-MMU-9718020" "R-MMU-4224014" "R-MMU-8941234"
[5421] "R-MMU-1363328" "R-MMU-1363331" "R-MMU-187545"  "R-MMU-165680" 
[5425] "R-MMU-5653936" "R-MMU-5653968" "R-MMU-5653974" "R-MMU-5672010"
[5429] "R-MMU-5672817" "R-MMU-5672843" "R-MMU-5675790" "R-MMU-8952716"
[5433] "R-MMU-8952726" "R-MMU-264865"  "R-MMU-8868356" "R-MMU-416690" 
[5437] "R-MMU-6806966" "R-MMU-166538"  "R-MMU-166542"  "R-MMU-169895" 
[5441] "R-MMU-8938121" "R-MMU-174367"  "R-MMU-1467466" "R-MMU-382575" 
[5445]

In [10]:
%%R
rxn_knn_misclass_rate.nls <- list()
rxn_knn_ari.nls <- list()
rxn_knn_ecount.nls <- list()
rxn_pca.nls <- list()
count <- 0

In [11]:
%%R
toi_indices <- seq(1,length(tcdd_dose_detail.vec))
print(toi_indices)

  [1]   1   2   3   4   5   6   7   8   9  10  11  12  13  14  15  16  17  18
 [19]  19  20  21  22  23  24  25  26  27  28  29  30  31  32  33  34  35  36
 [37]  37  38  39  40  41  42  43  44  45  46  47  48  49  50  51  52  53  54
 [55]  55  56  57  58  59  60  61  62  63  64  65  66  67  68  69  70  71  72
 [73]  73  74  75  76  77  78  79  80  81  82  83  84  85  86  87  88  89  90
 [91]  91  92  93  94  95  96  97  98  99 100 101 102 103 104 105 106 107 108
[109] 109 110 111 112 113 114 115 116 117 118 119 120 121 122 123 124 125 126
[127] 127 128 129 130 131 132 133 134 135 136 137 138 139 140 141 142 143 144
[145] 145 146 147 148 149 150 151 152 153 154 155 156 157 158 159 160 161 162
[163] 163 164 165 166 167 168 169 170 171 172 173 174 175 176 177 178 179 180
[181] 181 182 183 184 185 186 187 188 189 190 191 192 193 194 195 196 197 198
[199] 199 200 201 202 203 204 205 206 207 208 209 210 211 212 213 214 215 216
[217] 217 218 219 220 221 222 223 224 225 226 227 228 229 230 23

In [12]:
%%R
tcdd_dose_detail_vec_tis_of_interest <-
   tcdd_dose_detail.vec[toi_indices]
print(tcdd_dose_detail_vec_tis_of_interest)

  [1]  0.00  0.00  0.00  0.00  0.00 30.00 30.00 30.00 30.00 30.00 30.00  0.00
 [13]  0.00  0.00  0.00  0.00  0.00 30.00 30.00 30.00 30.00 30.00 30.00  0.00
 [25]  0.00  0.00  0.00  0.00  0.00 30.00 30.00 30.00 30.00 30.00 30.00  0.00
 [37]  0.00  0.00  0.00  0.00  0.00 30.00 30.00 30.00 30.00 30.00 30.00  0.00
 [49]  0.00  0.00  0.00  0.00 30.00 30.00 30.00 30.00 30.00  0.00  0.00  0.00
 [61]  0.00  0.00  0.00 30.00 30.00 30.00 30.00 30.00 30.00  0.00  0.00  0.00
 [73]  0.00 30.00 30.00 30.00 30.00 30.00 30.00  0.00  0.00  0.00  0.00  0.00
 [85]  0.00 30.00 30.00 30.00 30.00 30.00 30.00  0.00  0.00 30.00  0.00  0.00
 [97]  0.00  0.00  0.00  0.00  0.00  0.00  0.01  0.01  0.01  0.01  0.01  0.01
[109]  0.01  0.01  0.01  0.01  0.03  0.03  0.03  0.30  0.30  0.30  0.30  0.30
[121]  1.00  1.00  1.00  1.00  1.00  1.00  1.00  1.00  3.00  3.00  3.00  3.00
[133]  3.00  3.00  0.00  0.00  0.00  0.01  0.03  0.03  0.03  0.03  0.03  0.03
[145]  0.03  0.03  0.10  0.10  0.10  0.10  0.10  0.10  0.10  0.1

In [13]:
%%R
vst.count.mtx.tis_of_interest <- vst.count.mtx[, toi_indices]
print(vst.count.mtx.tis_of_interest)

                   SRR7817611 SRR7817612 SRR7817614 SRR7817615 SRR7817616
ENSMUSG00000000568   19.89468   19.78997   20.06086   19.95841   20.04601
ENSMUSG00000000579   14.61781   14.33031   13.94108   14.68931   14.69199
ENSMUSG00000000581   19.94625   19.81636   20.47749   20.14210   19.99506
ENSMUSG00000000594   21.83221   21.84224   22.10274   21.38252   21.38118
ENSMUSG00000000605   20.74409   20.59634   20.98925   20.92454   20.89263
ENSMUSG00000000617   13.27759   13.27740   13.27512   13.27749   13.27749
ENSMUSG00000000627   14.15261   13.73399   13.27512   13.27749   13.27749
ENSMUSG00000000628   15.44773   15.14633   14.33818   15.06463   15.24083
ENSMUSG00000000673   24.55927   24.56579   24.78833   24.55693   24.56123
ENSMUSG00000000682   16.20645   16.44576   15.95735   15.95630   15.85783
ENSMUSG00000000693   16.86627   16.63537   16.77325   16.86020   17.01999
ENSMUSG00000000706   13.27759   13.27740   13.27512   13.27749   13.27749
ENSMUSG00000000708   20.66120   20.522

ENSMUSG00000001964   17.84905   17.91074   18.38487   18.10191   18.11975
ENSMUSG00000001983   18.69588   18.52065   18.39797   18.75286   18.68914
ENSMUSG00000001985   13.27759   13.27740   13.27512   13.73596   13.27749
ENSMUSG00000001986   14.75954   15.17436   13.82776   14.55149   14.47753
ENSMUSG00000001998   16.90794   16.52293   16.82844   16.90043   16.71495
ENSMUSG00000001999   17.51444   17.31027   17.52006   17.12726   17.31699
ENSMUSG00000002010   21.19274   21.18099   21.07700   21.43019   21.41839
ENSMUSG00000002015   21.91197   21.93317   22.29460   21.89818   21.90990
ENSMUSG00000002020   14.97159   15.22056   14.39876   15.45209   15.25424
ENSMUSG00000002028   19.20020   19.24224   19.37672   19.53171   19.32265
ENSMUSG00000002031   18.52428   18.56078   19.13410   18.85978   18.60698
ENSMUSG00000002033   14.59788   14.62254   14.12364   14.79425   14.80238
ENSMUSG00000002043   17.14960   17.49627   17.49595   17.06179   16.81114
ENSMUSG00000002052   20.69542   20.619

ENSMUSG00000003099   20.31271   20.40871   20.34242   20.42305   20.32416
ENSMUSG00000003119   18.11570   18.13697   18.49143   18.30233   18.24035
ENSMUSG00000003131   19.44000   19.48471   19.22749   19.29958   19.37847
ENSMUSG00000003135   18.47742   18.22564   18.71653   18.40193   18.52470
ENSMUSG00000003153   14.97562   14.48630   14.39994   14.49054   14.56132
ENSMUSG00000003161   18.98990   19.04794   19.21236   19.09875   19.03193
ENSMUSG00000003184   20.97977   20.72307   20.92577   20.90850   20.88142
ENSMUSG00000003200   18.70344   18.65560   18.70031   18.73903   18.88083
ENSMUSG00000003206   14.49854   14.42211   14.83504   14.75048   14.56132
ENSMUSG00000003360   20.48335   20.61965   20.36474   20.65304   20.86778
ENSMUSG00000003435   21.42726   21.38884   20.82677   21.21745   21.19194
ENSMUSG00000003436   13.27759   13.27740   13.27512   13.27749   13.27749
ENSMUSG00000003437   19.59776   19.39917   19.60407   19.33809   19.03449
ENSMUSG00000003444   16.04801   15.605

ENSMUSG00000001494   13.68889   13.27551   13.67059   13.27443   13.27314
ENSMUSG00000001504   13.27555   13.27551   13.27456   13.27443   13.27314
ENSMUSG00000001506   21.71311   21.70666   21.33951   21.48232   22.29267
ENSMUSG00000001507   17.83878   17.97587   17.37636   17.63278   19.77759
ENSMUSG00000001517   16.29145   15.80148   15.97001   16.00418   15.74151
ENSMUSG00000001518   17.76462   17.70694   17.46305   17.35906   17.99654
ENSMUSG00000001521   16.05937   16.12743   15.45160   15.76441   16.62220
ENSMUSG00000001524   18.09090   18.22228   17.27396   17.00117   16.90120
ENSMUSG00000001542   17.86578   18.01443   20.24822   20.10207   20.14149
ENSMUSG00000001552   19.43770   19.24434   18.85568   19.00652   19.85693
ENSMUSG00000001622   13.27555   13.27551   14.09520   13.91414   13.76674
ENSMUSG00000001632   17.43400   17.54184   17.98210   17.98965   18.47964
ENSMUSG00000001642   16.65583   16.82218   16.01848   15.75750   16.47053
ENSMUSG00000001656   13.27555   13.275

ENSMUSG00000002699   16.89668   16.65553   17.44868   17.42989   17.30317
ENSMUSG00000002731   16.72267   16.71832   17.07534   16.95317   16.68193
ENSMUSG00000002733   17.31999   17.47163   18.36383   18.53604   18.67677
ENSMUSG00000002741   19.83305   20.01772   20.31933   20.12848   20.41300
ENSMUSG00000002748   19.87455   19.95772   21.08093   21.01784   20.63284
ENSMUSG00000002763   22.91324   22.85511   21.87391   21.82778   21.58466
ENSMUSG00000002767   21.13837   21.11538   18.95770   19.10290   18.79993
ENSMUSG00000002769   24.18902   24.21455   22.94514   22.91803   21.80053
ENSMUSG00000002771   14.36586   13.95629   13.91927   14.00658   14.19041
ENSMUSG00000002778   22.09736   22.02212   21.12661   21.04449   21.10218
ENSMUSG00000002797   17.19195   17.00538   16.70224   16.99308   15.86541
ENSMUSG00000002799   14.69358   14.47762   14.35632   14.34165   15.44674
ENSMUSG00000002803   17.88021   17.73652   16.91773   16.56645   16.28114
ENSMUSG00000002804   19.01841   19.101

...

ENSMUSG00000003555   18.95114   19.09239   18.12692   17.23105   17.03604
ENSMUSG00000003559   19.78496   19.60176   19.62798   18.94793   18.97099
ENSMUSG00000003573   16.47168   16.18766   16.86593   16.80782   16.68346
ENSMUSG00000003604   17.39373   17.47792   17.56663   17.07050   16.84489
ENSMUSG00000003617   25.50312   25.52384   25.39616   24.56358   24.58142
ENSMUSG00000003623   24.39254   24.36567   24.53836   24.61617   24.59912
ENSMUSG00000003644   18.64008   18.65132   19.13467   18.79061   18.79122
ENSMUSG00000003660   21.17623   21.14617   20.51142   21.13060   21.18550
ENSMUSG00000003665   13.27981   13.27981   13.27414   13.27187   13.27184
ENSMUSG00000003731   20.80605   20.75111   20.22056   20.50567   20.53000
ENSMUSG00000003746   23.21943   23.21446   23.16112   23.45243   23.43576
ENSMUSG00000003752   16.06954   16.10990   16.75798   16.43376   15.99937
ENSMUSG00000003779   15.52352   15.05838   16.20278   16.63163   16.94768
                   SRR4317653 SRR43176

ENSMUSG00000001827   13.68469   13.27525   13.76402   14.00011   13.81927
ENSMUSG00000001833   20.68261   20.46059   21.28306   21.29205   20.87650
ENSMUSG00000001847   21.68015   21.71262   21.71300   21.73604   21.66600
ENSMUSG00000001855   18.51618   18.39843   18.76798   18.69325   18.79129
ENSMUSG00000001865   13.27536   13.27525   13.53303   13.27063   13.67518
ENSMUSG00000001870   16.06502   16.31222   17.58876   17.66532   17.06866
ENSMUSG00000001891   23.35490   23.36156   24.99302   24.99215   24.70200
ENSMUSG00000001901   13.27536   13.27525   13.27040   13.27063   13.27493
ENSMUSG00000001918   17.82493   17.91239   19.84954   19.93560   20.08599
ENSMUSG00000001924   22.68443   22.61408   22.44143   22.42317   22.67681
ENSMUSG00000001930   17.97631   17.81715   19.02296   18.92605   18.22095
ENSMUSG00000001946   18.41679   17.96557   19.10528   19.21933   18.85631
ENSMUSG00000001962   17.46431   17.62826   17.27354   17.28303   17.06793
ENSMUSG00000001964   18.31434   18.473

ENSMUSG00000002985   28.20073   28.19864   27.07806   27.09759   27.25009
ENSMUSG00000002992   22.65911   22.56624   22.18158   22.14923   22.46696
ENSMUSG00000003031   20.75224   20.84147   20.72151   20.65945   20.84611
ENSMUSG00000003032   15.85450   15.88455   16.44746   16.27186   15.95994
ENSMUSG00000003033   18.68987   18.75463   19.11246   19.15558   19.09742
ENSMUSG00000003037   20.96196   21.06055   20.00451   19.95656   20.08912
ENSMUSG00000003039   19.82458   19.97240   20.16739   20.27711   20.39834
ENSMUSG00000003051   13.83527   14.04380   14.88080   15.17099   14.10245
ENSMUSG00000003053   26.60160   26.60734   20.66353   20.71392   24.49418
ENSMUSG00000003062   16.60598   16.63522   17.20084   17.16826   17.29111
ENSMUSG00000003068   20.87428   20.86149   19.85763   19.96309   20.23484
ENSMUSG00000003070   13.68824   13.83177   13.68499   13.58163   13.93350
ENSMUSG00000003072   21.78431   21.67224   21.58912   21.58912   21.62170
ENSMUSG00000003099   19.50341   19.572

ENSMUSG00000001632   18.39285   19.01354   19.09052
ENSMUSG00000001642   15.71726   16.44737   16.36909
ENSMUSG00000001656   13.27514   13.27243   13.27239
ENSMUSG00000001657   13.27514   13.27243   13.27239
ENSMUSG00000001663   19.57162   19.47091   19.51612
ENSMUSG00000001670   26.07109   26.05298   26.05059
ENSMUSG00000001729   20.93866   21.24753   21.34108
ENSMUSG00000001741   16.48882   17.21337   17.08286
ENSMUSG00000001750   20.45201   21.76892   21.72168
ENSMUSG00000001751   17.93951   17.80286   17.88597
ENSMUSG00000001755   22.11021   21.73021   21.75895
ENSMUSG00000001761   16.62807   17.16613   17.09925
ENSMUSG00000001767   17.89736   17.76131   17.81457
ENSMUSG00000001768   18.16129   18.64969   18.48289
ENSMUSG00000001773   13.27514   13.27243   13.27239
ENSMUSG00000001786   19.02041   18.96437   19.06585
ENSMUSG00000001794   21.56523   21.83162   21.87372
ENSMUSG00000001804   13.27514   13.27243   13.27239
ENSMUSG00000001827   14.03723   14.09496   13.82292
ENSMUSG00000

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [14]:
%%R
training_indices <-
   caret::createDataPartition(
      tcdd_dose_detail_vec_tis_of_interest,
      times = 1,
      p = 1.0, # no data will be held out when set to "1.0"
      list = FALSE
   )
print(training_indices)

       Resample1
  [1,]         1
  [2,]         2
  [3,]         3
  [4,]         4
  [5,]         5
  [6,]         6
  [7,]         7
  [8,]         8
  [9,]         9
 [10,]        10
 [11,]        11
 [12,]        12
 [13,]        13
 [14,]        14
 [15,]        15
 [16,]        16
 [17,]        17
 [18,]        18
 [19,]        19
 [20,]        20
 [21,]        21
 [22,]        22
 [23,]        23
 [24,]        24
 [25,]        25
 [26,]        26
 [27,]        27
 [28,]        28
 [29,]        29
 [30,]        30
 [31,]        31
 [32,]        32
 [33,]        33
 [34,]        34
 [35,]        35
 [36,]        36
 [37,]        37
 [38,]        38
 [39,]        39
 [40,]        40
 [41,]        41
 [42,]        42
 [43,]        43
 [44,]        44
 [45,]        45
 [46,]        46
 [47,]        47
 [48,]        48
 [49,]        49
 [50,]        50
 [51,]        51
 [52,]        52
 [53,]        53
 [54,]        54
 [55,]        55
 [56,]        56
 [57,]        57
 [58,]        

In [15]:
%%R
vst.count.mtx.train <-
   vst.count.mtx.tis_of_interest[, training_indices] #9/10ths of data
vst.count.mtx.test  <-
   vst.count.mtx.tis_of_interest[, -training_indices] #1/10th of data

print(vst.count.mtx.train)
print(length(vst.count.mtx.test))

                   SRR7817611 SRR7817612 SRR7817614 SRR7817615 SRR7817616
ENSMUSG00000000568   19.89468   19.78997   20.06086   19.95841   20.04601
ENSMUSG00000000579   14.61781   14.33031   13.94108   14.68931   14.69199
ENSMUSG00000000581   19.94625   19.81636   20.47749   20.14210   19.99506
ENSMUSG00000000594   21.83221   21.84224   22.10274   21.38252   21.38118
ENSMUSG00000000605   20.74409   20.59634   20.98925   20.92454   20.89263
ENSMUSG00000000617   13.27759   13.27740   13.27512   13.27749   13.27749
ENSMUSG00000000627   14.15261   13.73399   13.27512   13.27749   13.27749
ENSMUSG00000000628   15.44773   15.14633   14.33818   15.06463   15.24083
ENSMUSG00000000673   24.55927   24.56579   24.78833   24.55693   24.56123
ENSMUSG00000000682   16.20645   16.44576   15.95735   15.95630   15.85783
ENSMUSG00000000693   16.86627   16.63537   16.77325   16.86020   17.01999
ENSMUSG00000000706   13.27759   13.27740   13.27512   13.27749   13.27749
ENSMUSG00000000708   20.66120   20.522

ENSMUSG00000001964   17.84905   17.91074   18.38487   18.10191   18.11975
ENSMUSG00000001983   18.69588   18.52065   18.39797   18.75286   18.68914
ENSMUSG00000001985   13.27759   13.27740   13.27512   13.73596   13.27749
ENSMUSG00000001986   14.75954   15.17436   13.82776   14.55149   14.47753
ENSMUSG00000001998   16.90794   16.52293   16.82844   16.90043   16.71495
ENSMUSG00000001999   17.51444   17.31027   17.52006   17.12726   17.31699
ENSMUSG00000002010   21.19274   21.18099   21.07700   21.43019   21.41839
ENSMUSG00000002015   21.91197   21.93317   22.29460   21.89818   21.90990
ENSMUSG00000002020   14.97159   15.22056   14.39876   15.45209   15.25424
ENSMUSG00000002028   19.20020   19.24224   19.37672   19.53171   19.32265
ENSMUSG00000002031   18.52428   18.56078   19.13410   18.85978   18.60698
ENSMUSG00000002033   14.59788   14.62254   14.12364   14.79425   14.80238
ENSMUSG00000002043   17.14960   17.49627   17.49595   17.06179   16.81114
ENSMUSG00000002052   20.69542   20.619

ENSMUSG00000003099   20.31271   20.40871   20.34242   20.42305   20.32416
ENSMUSG00000003119   18.11570   18.13697   18.49143   18.30233   18.24035
ENSMUSG00000003131   19.44000   19.48471   19.22749   19.29958   19.37847
ENSMUSG00000003135   18.47742   18.22564   18.71653   18.40193   18.52470
ENSMUSG00000003153   14.97562   14.48630   14.39994   14.49054   14.56132
ENSMUSG00000003161   18.98990   19.04794   19.21236   19.09875   19.03193
ENSMUSG00000003184   20.97977   20.72307   20.92577   20.90850   20.88142
ENSMUSG00000003200   18.70344   18.65560   18.70031   18.73903   18.88083
ENSMUSG00000003206   14.49854   14.42211   14.83504   14.75048   14.56132
ENSMUSG00000003360   20.48335   20.61965   20.36474   20.65304   20.86778
ENSMUSG00000003435   21.42726   21.38884   20.82677   21.21745   21.19194
ENSMUSG00000003436   13.27759   13.27740   13.27512   13.27749   13.27749
ENSMUSG00000003437   19.59776   19.39917   19.60407   19.33809   19.03449
ENSMUSG00000003444   16.04801   15.605

ENSMUSG00000001494   13.68889   13.27551   13.67059   13.27443   13.27314
ENSMUSG00000001504   13.27555   13.27551   13.27456   13.27443   13.27314
ENSMUSG00000001506   21.71311   21.70666   21.33951   21.48232   22.29267
ENSMUSG00000001507   17.83878   17.97587   17.37636   17.63278   19.77759
ENSMUSG00000001517   16.29145   15.80148   15.97001   16.00418   15.74151
ENSMUSG00000001518   17.76462   17.70694   17.46305   17.35906   17.99654
ENSMUSG00000001521   16.05937   16.12743   15.45160   15.76441   16.62220
ENSMUSG00000001524   18.09090   18.22228   17.27396   17.00117   16.90120
ENSMUSG00000001542   17.86578   18.01443   20.24822   20.10207   20.14149
ENSMUSG00000001552   19.43770   19.24434   18.85568   19.00652   19.85693
ENSMUSG00000001622   13.27555   13.27551   14.09520   13.91414   13.76674
ENSMUSG00000001632   17.43400   17.54184   17.98210   17.98965   18.47964
ENSMUSG00000001642   16.65583   16.82218   16.01848   15.75750   16.47053
ENSMUSG00000001656   13.27555   13.275

ENSMUSG00000002699   16.89668   16.65553   17.44868   17.42989   17.30317
ENSMUSG00000002731   16.72267   16.71832   17.07534   16.95317   16.68193
ENSMUSG00000002733   17.31999   17.47163   18.36383   18.53604   18.67677
ENSMUSG00000002741   19.83305   20.01772   20.31933   20.12848   20.41300
ENSMUSG00000002748   19.87455   19.95772   21.08093   21.01784   20.63284
ENSMUSG00000002763   22.91324   22.85511   21.87391   21.82778   21.58466
ENSMUSG00000002767   21.13837   21.11538   18.95770   19.10290   18.79993
ENSMUSG00000002769   24.18902   24.21455   22.94514   22.91803   21.80053
ENSMUSG00000002771   14.36586   13.95629   13.91927   14.00658   14.19041
ENSMUSG00000002778   22.09736   22.02212   21.12661   21.04449   21.10218
ENSMUSG00000002797   17.19195   17.00538   16.70224   16.99308   15.86541
ENSMUSG00000002799   14.69358   14.47762   14.35632   14.34165   15.44674
ENSMUSG00000002803   17.88021   17.73652   16.91773   16.56645   16.28114
ENSMUSG00000002804   19.01841   19.101

...

ENSMUSG00000003435   20.97477   21.13587   21.24001   20.42331   20.54192
ENSMUSG00000003436   13.27418   13.27431   13.27431   13.27476   13.27496
ENSMUSG00000003437   18.93189   19.09557   18.92470   19.16988   19.27475
ENSMUSG00000003444   16.30877   16.11131   16.19529   15.83228   16.01290
ENSMUSG00000003452   13.79380   14.00101   13.90936   13.81166   13.93067
ENSMUSG00000003458   20.48358   20.46346   20.51672   20.50315   20.36064
ENSMUSG00000003464   22.46391   22.47064   22.44640   22.59309   22.57754
ENSMUSG00000003476   14.13455   13.98185   13.80246   13.92701   13.82029
ENSMUSG00000003477   25.01121   24.21643   24.21538   24.90691   24.90517
ENSMUSG00000003484   14.02354   14.53385   14.48421   14.17958   14.52671
ENSMUSG00000003500   14.79587   15.53052   15.38846   15.21189   15.47485
ENSMUSG00000003505   13.27418   13.27431   13.27431   13.27476   13.27496
ENSMUSG00000003518   20.08130   20.41503   20.58938   20.47829   20.54703
ENSMUSG00000003526   23.40201   23.017

ENSMUSG00000001622   13.27726   13.27755   13.27498   13.27407   13.27883
ENSMUSG00000001632   18.01193   18.00985   18.10136   18.10213   17.99083
ENSMUSG00000001642   15.04063   15.55413   15.56010   16.07185   15.74009
ENSMUSG00000001656   13.27726   13.27755   13.27498   13.27407   13.27883
ENSMUSG00000001657   13.27726   13.27755   13.27498   13.27407   13.27883
ENSMUSG00000001663   22.93927   23.01725   22.88464   22.08699   23.05522
ENSMUSG00000001670   25.87542   25.87429   25.82313   25.63501   26.52495
ENSMUSG00000001729   20.04678   20.05329   19.81925   20.27364   19.97676
ENSMUSG00000001741   15.82669   15.69961   15.99963   16.12764   16.19122
ENSMUSG00000001750   19.52830   19.39842   19.87643   20.57949   20.49051
ENSMUSG00000001751   18.64385   18.37910   18.83833   18.57970   18.82875
ENSMUSG00000001755   22.24821   22.30664   22.48932   22.44481   21.82751
ENSMUSG00000001761   15.92958   15.96118   15.98159   15.81343   16.85746
ENSMUSG00000001767   17.90018   17.866

ENSMUSG00000002797   16.53047   16.60058   16.93267   16.90041   16.97914
ENSMUSG00000002799   13.89622   14.03823   14.19348   13.89650   13.27883
ENSMUSG00000002803   17.43348   17.35261   17.21636   17.34691   17.75637
ENSMUSG00000002804   16.57176   16.56645   17.92259   17.69346   17.40211
ENSMUSG00000002814   16.69042   16.66369   16.54836   16.47849   17.39942
ENSMUSG00000002820   19.76612   19.54336   19.80515   19.92689   19.62036
ENSMUSG00000002846   18.44426   18.72756   18.82860   18.64000   18.80929
ENSMUSG00000002847   19.57787   19.70380   19.21644   18.53818   20.56768
ENSMUSG00000002870   15.44451   15.49610   15.48018   15.92866   15.52126
ENSMUSG00000002885   17.93214   17.67679   18.19174   19.14977   18.80453
ENSMUSG00000002900   16.41079   16.56771   16.37618   17.13785   17.26944
ENSMUSG00000002908   16.29039   16.03439   16.14581   15.72785   15.84110
ENSMUSG00000002944   23.51044   23.45398   23.51680   23.43993   20.88401
ENSMUSG00000002948   20.29554   20.233

ENSMUSG00000000901   15.50028   15.44548   16.15008   16.11359   15.92034
ENSMUSG00000000902   17.53122   17.59804   17.89097   18.13698   17.94578
ENSMUSG00000000903   13.77431   13.27930   13.72948   13.27719   13.81681
ENSMUSG00000000915   19.37118   19.44238   20.19863   20.05341   19.87992
ENSMUSG00000000942   13.27918   13.77721   14.02427   13.27719   13.81924
ENSMUSG00000000957   19.17908   19.45996   19.64948   19.42710   19.26507
ENSMUSG00000000958   15.70087   15.92730   16.11274   16.07456   15.67876
ENSMUSG00000000959   19.76110   19.61703   20.19194   20.01274   19.68739
ENSMUSG00000000982   13.95977   13.27930   13.27720   13.72922   13.27485
ENSMUSG00000001014   14.51571   14.10763   14.60677   14.39828   14.53261
ENSMUSG00000001016   18.57170   18.85060   18.85652   18.46278   18.79139
ENSMUSG00000001017   20.52356   20.39397   20.35653   20.40788   20.48934
ENSMUSG00000001280   20.84093   20.69448   20.55803   20.60335   20.61493
ENSMUSG00000001281   14.51229   14.892

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [16]:
%%R
tcdd_dose_detail.vec.train <-
   tcdd_dose_detail_vec_tis_of_interest[training_indices]
tcdd_dose_detail.vec.test <-
   tcdd_dose_detail_vec_tis_of_interest[-training_indices]

# print(gtex_tissue_detail.vec.train)
print(length(unique(tcdd_dose_detail.vec.train)))

In [17]:
%%R
saveRDS(tcdd_dose_detail.vec.train,file=paste(OUT_DIR,"tcdd_dose_detail_vec_train.Rds",sep=""))

In [18]:
%%R
cv_fold_indices <- caret::createFolds(tcdd_dose_detail.vec.train,
                                      k = N_FOLDS)
print(cv_fold_indices)

$Fold01
 [1]  24  25  38  45  47  52  67 114 115 119 122 125 138 144 152 172 177 178 190
[20] 193 203 214 215 217 220 223 247 248 287 307 308 314 319 330 340 341 366 369

$Fold02
 [1]   2  14  19  40  44  48  56  61  65  66  73  89  96 103 108 131 132 157 161
[20] 163 165 166 196 228 234 243 253 258 260 270 285 288 290 292 293 311 343 344

$Fold03
 [1]   9  37  42  46  50  54  72  74  78  84 109 110 127 130 133 141 142 148 175
[20] 186 191 225 244 256 263 269 271 272 297 301 321 332 333 349 359 362 367 379
[39] 383

$Fold04
 [1]  22  51  55  58  59  68  76  79  85  88  92 107 121 135 147 167 168 169 173
[20] 176 179 182 187 221 222 229 267 273 284 294 298 300 336 338 352 356 363 365

$Fold05
 [1]   8  11  30  60  70  77  81  86  93  98 101 113 123 126 129 140 155 159 162
[20] 205 206 210 233 237 240 245 251 252 257 266 275 279 286 299 320 360 368 371
[39] 374

$Fold06
 [1]   1   5  21  23  28  41  43  62  64  71  80 116 124 134 146 156 174 180 181
[20] 195 230 262 264 268 276 278 280 2

In [19]:
%%R
binary_tcdd_dose_annotations <- unique(tcdd_dose_detail.vec)
print(binary_tcdd_dose_annotations)

[1]  0.00 30.00  0.01  0.03  0.30  1.00  3.00  0.10 10.00


In [20]:
%%R
full_rxn_pca_results.nls <- list()
rxn_id_2_result_file_idx.nls <- list()

In [22]:
%%R
print(vst.count.mtx.train)

                   SRR7817611 SRR7817612 SRR7817614 SRR7817615 SRR7817616
ENSMUSG00000000568   19.89468   19.78997   20.06086   19.95841   20.04601
ENSMUSG00000000579   14.61781   14.33031   13.94108   14.68931   14.69199
ENSMUSG00000000581   19.94625   19.81636   20.47749   20.14210   19.99506
ENSMUSG00000000594   21.83221   21.84224   22.10274   21.38252   21.38118
ENSMUSG00000000605   20.74409   20.59634   20.98925   20.92454   20.89263
ENSMUSG00000000617   13.27759   13.27740   13.27512   13.27749   13.27749
ENSMUSG00000000627   14.15261   13.73399   13.27512   13.27749   13.27749
ENSMUSG00000000628   15.44773   15.14633   14.33818   15.06463   15.24083
ENSMUSG00000000673   24.55927   24.56579   24.78833   24.55693   24.56123
ENSMUSG00000000682   16.20645   16.44576   15.95735   15.95630   15.85783
ENSMUSG00000000693   16.86627   16.63537   16.77325   16.86020   17.01999
ENSMUSG00000000706   13.27759   13.27740   13.27512   13.27749   13.27749
ENSMUSG00000000708   20.66120   20.522

ENSMUSG00000001964   17.84905   17.91074   18.38487   18.10191   18.11975
ENSMUSG00000001983   18.69588   18.52065   18.39797   18.75286   18.68914
ENSMUSG00000001985   13.27759   13.27740   13.27512   13.73596   13.27749
ENSMUSG00000001986   14.75954   15.17436   13.82776   14.55149   14.47753
ENSMUSG00000001998   16.90794   16.52293   16.82844   16.90043   16.71495
ENSMUSG00000001999   17.51444   17.31027   17.52006   17.12726   17.31699
ENSMUSG00000002010   21.19274   21.18099   21.07700   21.43019   21.41839
ENSMUSG00000002015   21.91197   21.93317   22.29460   21.89818   21.90990
ENSMUSG00000002020   14.97159   15.22056   14.39876   15.45209   15.25424
ENSMUSG00000002028   19.20020   19.24224   19.37672   19.53171   19.32265
ENSMUSG00000002031   18.52428   18.56078   19.13410   18.85978   18.60698
ENSMUSG00000002033   14.59788   14.62254   14.12364   14.79425   14.80238
ENSMUSG00000002043   17.14960   17.49627   17.49595   17.06179   16.81114
ENSMUSG00000002052   20.69542   20.619

ENSMUSG00000003099   20.31271   20.40871   20.34242   20.42305   20.32416
ENSMUSG00000003119   18.11570   18.13697   18.49143   18.30233   18.24035
ENSMUSG00000003131   19.44000   19.48471   19.22749   19.29958   19.37847
ENSMUSG00000003135   18.47742   18.22564   18.71653   18.40193   18.52470
ENSMUSG00000003153   14.97562   14.48630   14.39994   14.49054   14.56132
ENSMUSG00000003161   18.98990   19.04794   19.21236   19.09875   19.03193
ENSMUSG00000003184   20.97977   20.72307   20.92577   20.90850   20.88142
ENSMUSG00000003200   18.70344   18.65560   18.70031   18.73903   18.88083
ENSMUSG00000003206   14.49854   14.42211   14.83504   14.75048   14.56132
ENSMUSG00000003360   20.48335   20.61965   20.36474   20.65304   20.86778
ENSMUSG00000003435   21.42726   21.38884   20.82677   21.21745   21.19194
ENSMUSG00000003436   13.27759   13.27740   13.27512   13.27749   13.27749
ENSMUSG00000003437   19.59776   19.39917   19.60407   19.33809   19.03449
ENSMUSG00000003444   16.04801   15.605

ENSMUSG00000001494   13.68889   13.27551   13.67059   13.27443   13.27314
ENSMUSG00000001504   13.27555   13.27551   13.27456   13.27443   13.27314
ENSMUSG00000001506   21.71311   21.70666   21.33951   21.48232   22.29267
ENSMUSG00000001507   17.83878   17.97587   17.37636   17.63278   19.77759
ENSMUSG00000001517   16.29145   15.80148   15.97001   16.00418   15.74151
ENSMUSG00000001518   17.76462   17.70694   17.46305   17.35906   17.99654
ENSMUSG00000001521   16.05937   16.12743   15.45160   15.76441   16.62220
ENSMUSG00000001524   18.09090   18.22228   17.27396   17.00117   16.90120
ENSMUSG00000001542   17.86578   18.01443   20.24822   20.10207   20.14149
ENSMUSG00000001552   19.43770   19.24434   18.85568   19.00652   19.85693
ENSMUSG00000001622   13.27555   13.27551   14.09520   13.91414   13.76674
ENSMUSG00000001632   17.43400   17.54184   17.98210   17.98965   18.47964
ENSMUSG00000001642   16.65583   16.82218   16.01848   15.75750   16.47053
ENSMUSG00000001656   13.27555   13.275

ENSMUSG00000002699   16.89668   16.65553   17.44868   17.42989   17.30317
ENSMUSG00000002731   16.72267   16.71832   17.07534   16.95317   16.68193
ENSMUSG00000002733   17.31999   17.47163   18.36383   18.53604   18.67677
ENSMUSG00000002741   19.83305   20.01772   20.31933   20.12848   20.41300
ENSMUSG00000002748   19.87455   19.95772   21.08093   21.01784   20.63284
ENSMUSG00000002763   22.91324   22.85511   21.87391   21.82778   21.58466
ENSMUSG00000002767   21.13837   21.11538   18.95770   19.10290   18.79993
ENSMUSG00000002769   24.18902   24.21455   22.94514   22.91803   21.80053
ENSMUSG00000002771   14.36586   13.95629   13.91927   14.00658   14.19041
ENSMUSG00000002778   22.09736   22.02212   21.12661   21.04449   21.10218
ENSMUSG00000002797   17.19195   17.00538   16.70224   16.99308   15.86541
ENSMUSG00000002799   14.69358   14.47762   14.35632   14.34165   15.44674
ENSMUSG00000002803   17.88021   17.73652   16.91773   16.56645   16.28114
ENSMUSG00000002804   19.01841   19.101

...

ENSMUSG00000000708   21.35107   21.35283   21.15443   21.19191   21.07858
ENSMUSG00000000711   21.08762   21.01994   20.48200   20.53886   20.79241
ENSMUSG00000000730   13.27650   13.27676   13.27579   13.27581   13.27495
ENSMUSG00000000732   14.52724   13.88003   14.26735   14.56130   14.31940
ENSMUSG00000000738   20.00757   19.97862   19.75940   19.60298   20.05761
ENSMUSG00000000740   16.89001   16.98599   18.34949   18.63067   17.53783
ENSMUSG00000000751   19.85951   19.90558   20.01306   19.99232   20.05723
ENSMUSG00000000759   18.87120   18.75669   18.38504   18.34192   18.49321
ENSMUSG00000000766   13.27650   13.27676   13.27579   13.27581   13.67205
ENSMUSG00000000776   16.56478   16.29643   17.02275   16.85596   16.57246
ENSMUSG00000000782   15.96069   15.98131   16.15491   16.07922   15.43868
ENSMUSG00000000787   23.17905   23.17237   22.66388   22.66429   22.96154
ENSMUSG00000000791   14.66011   14.79892   15.35997   15.33437   15.43205
ENSMUSG00000000792   13.27650   13.276

ENSMUSG00000002052   20.64280   20.57581   20.19373   20.09168   20.58218
ENSMUSG00000002059   15.13756   15.07460   14.48567   14.66444   15.51376
ENSMUSG00000002068   14.42722   14.80100   14.84830   14.79816   14.57959
ENSMUSG00000002100   13.71363   13.71951   13.69775   13.27581   13.82231
ENSMUSG00000002102   22.21487   22.23832   22.29341   22.24790   22.25223
ENSMUSG00000002108   21.70353   21.70346   21.44565   21.31718   21.58706
ENSMUSG00000002109   18.57833   18.59196   18.42805   18.06007   18.37526
ENSMUSG00000002111   15.71761   15.37168   15.90128   15.92389   15.61646
ENSMUSG00000002129   18.87462   18.75237   19.02542   19.02907   18.86860
ENSMUSG00000002147   20.80111   20.81449   20.62492   20.57627   20.45111
ENSMUSG00000002204   14.40350   13.98998   14.63693   14.35546   14.40809
ENSMUSG00000002205   18.91566   18.82426   18.99644   19.02532   18.98094
ENSMUSG00000002210   17.41672   17.42351   17.00481   17.39876   17.18842
ENSMUSG00000002221   18.61082   18.595

ENSMUSG00000003444   16.50403   16.63602   16.38404   16.29044   16.17230
ENSMUSG00000003452   13.60601   13.27676   13.94757   13.69817   14.03002
ENSMUSG00000003458   20.67473   20.52798   20.32040   20.14811   20.50111
ENSMUSG00000003464   22.77500   22.79456   22.66347   22.64478   22.81035
ENSMUSG00000003476   13.78953   13.79659   13.84621   13.92089   13.27495
ENSMUSG00000003477   24.87813   24.89037   24.71359   24.68307   24.46340
ENSMUSG00000003484   13.87155   13.85155   14.02577   14.48582   14.31557
ENSMUSG00000003500   15.08136   14.85087   15.92159   15.78938   15.18807
ENSMUSG00000003505   13.27650   13.27676   13.27579   13.27581   13.27495
ENSMUSG00000003518   20.57756   20.42830   20.80129   20.73251   20.53169
ENSMUSG00000003526   23.40501   23.40580   23.52107   23.59214   23.47537
ENSMUSG00000003528   22.40834   22.36792   22.75979   22.71753   22.48020
ENSMUSG00000003534   15.05290   15.02129   14.52572   14.76623   14.59832
ENSMUSG00000003541   15.48855   15.821

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



   18.66527   17.79098   17.75994
ENSMUSG00000001473   18.09455   18.99229   18.93301
ENSMUSG00000001494   13.27514   13.74125   13.27239
ENSMUSG00000001504   13.27514   13.27243   13.27239
ENSMUSG00000001506   21.75669   22.65468   22.57800
ENSMUSG00000001507   17.51233   18.45186   18.67765

In [23]:
%%R
n_rxns <- length(rxns)
print(n_rxns)
result_idx <- 1
for(rxn_id_idx in seq(1:n_rxns)){
   rxn_id <- rxns[rxn_id_idx]
   rxn_pca <-
      prcomp(t(vst.count.mtx.train[rxn2ensembls.nls[[rxn_id]], ]), scale. = T)
   full_rxn_pca_results.nls[[rxn_id]] <- rxn_pca
   rxn_id_2_result_file_idx.nls[[rxn_id]] <- result_idx
   rxn_pca.nls[[rxn_id]] <-
      rxn_pca$x[, 1] # 1st principal component coordinate within this reaction-space for each sample
   if(mod(rxn_id_idx,100) == 0){
      print(paste("Processed ",rxn_id_idx,
                  " of ",n_rxns,
                  " reactions (",round((rxn_id_idx + 1)/n_rxns,digits = 3) * 100,"%)...",
                  sep=""))
      flush.console()
   }
   if(mod(rxn_id_idx,1000) == 0){
      print(paste("Storing PCA objects containing reactions ",rxn_id_idx-1000,
                  "-",rxn_id_idx,
                  " of ",n_rxns,
                  " reactions (",round((rxn_id_idx + 1)/n_rxns,digits = 3) * 100,"%)...",
                  sep=""))
      saveRDS(full_rxn_pca_results.nls,
              paste(OUT_DIR, "full_rxn_pca_results_nls",rxn_id_idx-1000,
                    "-",rxn_id_idx,".Rds", sep=""))
      full_rxn_pca_results.nls <- list()
      gc()
      result_idx <- result_idx + 1
   }
}

[1] "Processed 500 of 7839 reactions (6.4%)..."
[1] "Processed 600 of 7839 reactions (7.7%)..."
[1] "Processed 700 of 7839 reactions (8.9%)..."
[1] "Processed 800 of 7839 reactions (10.2%)..."
[1] "Processed 900 of 7839 reactions (11.5%)..."
[1] "Processed 1000 of 7839 reactions (12.8%)..."
[1] "Storing PCA objects containing reactions 0-1000 of 7839 reactions (12.8%)..."
[1] "Processed 1100 of 7839 reactions (14%)..."
[1] "Processed 1200 of 7839 reactions (15.3%)..."
[1] "Processed 1300 of 7839 reactions (16.6%)..."
[1] "Processed 1400 of 7839 reactions (17.9%)..."
[1] "Processed 1500 of 7839 reactions (19.1%)..."
[1] "Processed 1600 of 7839 reactions (20.4%)..."
[1] "Processed 1700 of 7839 reactions (21.7%)..."
[1] "Processed 1800 of 7839 reactions (23%)..."
[1] "Processed 1900 of 7839 reactions (24.3%)..."
[1] "Processed 2000 of 7839 reactions (25.5%)..."
[1] "Storing PCA objects containing reactions 1000-2000 of 7839 reactions (25.5%)..."
[1] "Processed 2100 of 7839 reactions (26.8

In [24]:
%%R
# store remaining PCA objects and removing from RAM
saveRDS(rxn_id_2_result_file_idx.nls,
        paste(OUT_DIR,"rxn_id_2_result_file_idx_nls.Rds",sep=""))
saveRDS(full_rxn_pca_results.nls,
        paste(OUT_DIR, "full_rxn_pca_results_nls.Rds", sep=""))
rm(full_rxn_pca_results.nls)
gc()

           used  (Mb) gc trigger  (Mb) max used  (Mb)
Ncells  6936085 370.5   10062812 537.5 10062812 537.5
Vcells 21921061 167.3   40359668 308.0 32125989 245.2


In [25]:
%%R
# compare informaction content of below files with pca plots or similar
saveRDS(rxn_pca.nls, paste(OUT_DIR, "rxn_pca_nls.Rds", sep = ""))
saveRDS(vst.count.mtx.train,
        paste(OUT_DIR, "vst_count_mtx_train.Rds", sep = ""))

In [26]:
%%R
for (cv_fold in names(cv_fold_indices)) {
  cur_cv_fold_indices <- cv_fold_indices[[cv_fold]]
  print(cur_cv_fold_indices)
  print("----------")
}

 [1]  24  25  38  45  47  52  67 114 115 119 122 125 138 144 152 172 177 178 190
[20] 193 203 214 215 217 220 223 247 248 287 307 308 314 319 330 340 341 366 369
[1] "----------"
 [1]   2  14  19  40  44  48  56  61  65  66  73  89  96 103 108 131 132 157 161
[20] 163 165 166 196 228 234 243 253 258 260 270 285 288 290 292 293 311 343 344
[1] "----------"
 [1]   9  37  42  46  50  54  72  74  78  84 109 110 127 130 133 141 142 148 175
[20] 186 191 225 244 256 263 269 271 272 297 301 321 332 333 349 359 362 367 379
[39] 383
[1] "----------"
 [1]  22  51  55  58  59  68  76  79  85  88  92 107 121 135 147 167 168 169 173
[20] 176 179 182 187 221 222 229 267 273 284 294 298 300 336 338 352 356 363 365
[1] "----------"
 [1]   8  11  30  60  70  77  81  86  93  98 101 113 123 126 129 140 155 159 162
[20] 205 206 210 233 237 240 245 251 252 257 266 275 279 286 299 320 360 368 371
[39] 374
[1] "----------"
 [1]   1   5  21  23  28  41  43  62  64  71  80 116 124 134 146 156 174 180 181
[20] 1

In [27]:
%%R
# print(tissue_annotation)
# print(binary_tcdd_dose_annotations)
# print(paste("Processing tissue annotation:", tissue_annotation))
# print(length(binary_tcdd_dose_detail_vec.test.cv_test_list))
# print(sum(tcdd_dose_detail.vec.train.cv_test == tissue_annotation))
# print(length(rxns))

# binary_tcdd_dose_annotations <- c(0.00, 30.00, 0.01, 0.03, 0.10, 0.30, 1.00, 3.00, 10.00)

formatted_annotations <- format(binary_tcdd_dose_annotations, nsmall = 2)

formatted_annotations <- trimws(formatted_annotations)

binary_tcdd_dose_annotations <- formatted_annotations

print(binary_tcdd_dose_annotations)
for (annotation in binary_tcdd_dose_annotations) {
    print(annotation)
}

[1] "0.00"  "30.00" "0.01"  "0.03"  "0.30"  "1.00"  "3.00"  "0.10"  "10.00"
[1] "0.00"
[1] "30.00"
[1] "0.01"
[1] "0.03"
[1] "0.30"
[1] "1.00"
[1] "3.00"
[1] "0.10"
[1] "10.00"


In [28]:
%%R
# main loop
for (rxn_id_idx in seq(1:length(rxns))) {
   rxn_id <- rxns[rxn_id_idx]
   ensembl_ids <- rxn2ensembls.nls[[rxn_id]]
   
   mean_misclass_rate <- list()
   sum_ari <- 0

   for (cv_fold in names(cv_fold_indices)) {
      cur_cv_fold_indices <- cv_fold_indices[[cv_fold]]
      
      vst.count.mtx.train.cv_train <-
         vst.count.mtx.train[, -cur_cv_fold_indices] # 4/5ths of training features
      vst.count.mtx.train.cv_test <-
         vst.count.mtx.train[, cur_cv_fold_indices] # 1/5th of training features
      
      tcdd_dose_detail.vec.train.cv_train <-
         tcdd_dose_detail.vec.train[-cur_cv_fold_indices] # 4/5ths of training labels
      tcdd_dose_detail.vec.train.cv_test <-
         tcdd_dose_detail.vec.train[cur_cv_fold_indices] # 1/5th of training labels
       
      binary_tcdd_dose_detail_vec.test.cv_test_list <- list()
      for (tissue_annotation in binary_tcdd_dose_annotations) {
         binary_tcdd_dose_detail_vec.test.cv_test_list[[as.character(tissue_annotation)]] <-
            (as.character(tcdd_dose_detail.vec.train.cv_test) == as.character(tissue_annotation))
      }
      
      cv_train.expr_mat <-
         t(vst.count.mtx.train.cv_train[ensembl_ids, ])
      cv_test.expr_mat <-
         t(vst.count.mtx.train.cv_test[ensembl_ids, ])

      rxn_knn_calls <- class::knn(train = cv_train.expr_mat,
                                  test = cv_test.expr_mat,
                                  cl = tcdd_dose_detail.vec.train.cv_train)
      
      # calculate & store adjusted rand index
      cur_ari <- pdfCluster::adj.rand.index(rxn_knn_calls,
                                            tcdd_dose_detail.vec.train.cv_test)
      sum_ari <- cur_ari + sum_ari
      
      # for each tissue, calculate misclassification rate
      for (tissue_annotation in binary_tcdd_dose_annotations) {
         cur_rxn_knn_calls <- (rxn_knn_calls == tissue_annotation)
            
         
         tab <- table(cur_rxn_knn_calls,
                      binary_tcdd_dose_detail_vec.test.cv_test_list[[tissue_annotation]])

         cur_misclass_rate <- 1 - sum(diag(tab)) / sum(tab)
         sum_misclass_rate <- cur_misclass_rate
         if (!is.null(mean_misclass_rate[[tissue_annotation]])) {
           sum_misclass_rate <- sum_misclass_rate + mean_misclass_rate[[tissue_annotation]]
         }
         mean_misclass_rate[[tissue_annotation]] <- sum_misclass_rate
      }
   }
   for(tissue_annotation in binary_tcdd_dose_annotations){
      mean_misclass_rate[[tissue_annotation]] <- (mean_misclass_rate[[tissue_annotation]] / N_FOLDS)
   }
   mean_ari <- sum_ari / N_FOLDS
   ecount <- length(ensembl_ids)
   
   rxn_knn_misclass_rate.nls[[rxn_id]] <- mean_misclass_rate
   assign("mean_misclass_rate",NULL,envir = .GlobalEnv)
   
   rxn_knn_ari.nls[[rxn_id]] <- mean_ari
   rxn_knn_ecount.nls[[rxn_id]] <- ecount
   
   count <- count + 1
   if (mod(count, 10) == 0) {
      print(
         paste(
            "Last RXN_ID = ",
            rxn_id,
            ": Last ARI = ",
            mean_ari,
            ": Last ECOUNT = ",
            ecount,
            ": Last Lung MISCLASS = ",
            rxn_knn_misclass_rate.nls[[rxn_id]][["Lung"]],
            ": Last Uterus MISCLASS = ",
            rxn_knn_misclass_rate.nls[[rxn_id]][["Uterus"]],
            ". Now ",
            round(1.0 - count / length(rxns),3) * 100,
            "% remaining..."
         )
      )
      flush.console()
   }
}

[1] "Last RXN_ID =  R-MMU-6798748 : Last ARI =  0.895544755014278 : Last ECOUNT =  55 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  99.9 % remaining..."
[1] "Last RXN_ID =  R-MMU-9840884 : Last ARI =  0.556532409197132 : Last ECOUNT =  3 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  99.7 % remaining..."
[1] "Last RXN_ID =  R-MMU-2002466 : Last ARI =  0.504184461320664 : Last ECOUNT =  5 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  99.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-2247925 : Last ARI =  0.116703743917538 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  99.5 % remaining..."
[1] "Last RXN_ID =  R-MMU-9016782 : Last ARI =  0.116703743917538 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  99.4 % remaining..."
[1] "Last RXN_ID =  R-MMU-8871193 : Last ARI =  0.904204104588323 : Last ECOUNT =  65 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  99.2 % remaining..."
[1] "Las

[1] "Last RXN_ID =  R-MMU-9668419 : Last ARI =  0.63618032712355 : Last ECOUNT =  11 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  93.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-114671 : Last ARI =  0.355161447445995 : Last ECOUNT =  3 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  93.5 % remaining..."
[1] "Last RXN_ID =  R-MMU-2243926 : Last ARI =  0.339058570712783 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  93.4 % remaining..."
[1] "Last RXN_ID =  R-MMU-2395322 : Last ARI =  0.339058570712783 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  93.2 % remaining..."
[1] "Last RXN_ID =  R-MMU-430096 : Last ARI =  0.412685189362949 : Last ECOUNT =  4 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  93.1 % remaining..."
[1] "Last RXN_ID =  R-MMU-8985623 : Last ARI =  0.272195820780518 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  93 % remaining..."
[1] "Last RXN_

[1] "Last RXN_ID =  R-MMU-390593 : Last ARI =  0.384554389789904 : Last ECOUNT =  16 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  87.4 % remaining..."
[1] "Last RXN_ID =  R-MMU-264458 : Last ARI =  0.794858608998288 : Last ECOUNT =  17 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  87.2 % remaining..."
[1] "Last RXN_ID =  R-MMU-5610758 : Last ARI =  0.801639858409648 : Last ECOUNT =  17 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  87.1 % remaining..."
[1] "Last RXN_ID =  R-MMU-5689539 : Last ARI =  0.839046351673932 : Last ECOUNT =  16 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  87 % remaining..."
[1] "Last RXN_ID =  R-MMU-8866553 : Last ARI =  0.849352145300925 : Last ECOUNT =  21 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  86.9 % remaining..."
[1] "Last RXN_ID =  R-MMU-983150 : Last ARI =  0.849352145300925 : Last ECOUNT =  21 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  86.7 % remaining..."
[1] "Last

[1] "Last RXN_ID =  R-MMU-187506 : Last ARI =  0.0771857783012219 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  81.1 % remaining..."
[1] "Last RXN_ID =  R-MMU-9632873 : Last ARI =  0.0771857783012219 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  81 % remaining..."
[1] "Last RXN_ID =  R-MMU-432706 : Last ARI =  0.66281302961154 : Last ECOUNT =  10 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  80.9 % remaining..."
[1] "Last RXN_ID =  R-MMU-5623521 : Last ARI =  0.256237199986606 : Last ECOUNT =  6 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  80.7 % remaining..."
[1] "Last RXN_ID =  R-MMU-196126 : Last ARI =  0.0774220168831463 : Last ECOUNT =  3 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  80.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-164832 : Last ARI =  0.147167399440646 : Last ECOUNT =  4 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  80.5 % remaining..."
[1] "Last RXN

[1] "Last RXN_ID =  R-MMU-374758 : Last ARI =  0.0552676038525534 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  74.9 % remaining..."
[1] "Last RXN_ID =  R-MMU-8944254 : Last ARI =  0.0793711860273945 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  74.7 % remaining..."
[1] "Last RXN_ID =  R-MMU-141409 : Last ARI =  0.822698234362275 : Last ECOUNT =  53 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  74.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-2130349 : Last ARI =  0.49819500191494 : Last ECOUNT =  9 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  74.5 % remaining..."
[1] "Last RXN_ID =  R-MMU-449117 : Last ARI =  0.0741677248667339 : Last ECOUNT =  3 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  74.4 % remaining..."
[1] "Last RXN_ID =  R-MMU-5619428 : Last ARI =  0.500390396344645 : Last ECOUNT =  50 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  74.2 % remaining..."
[1] "Last

...

[1] "Last RXN_ID =  R-MMU-6784598 : Last ARI =  0.131064805787715 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  31.1 % remaining..."
[1] "Last RXN_ID =  R-MMU-2022399 : Last ARI =  0.488840237935881 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  31 % remaining..."
[1] "Last RXN_ID =  R-MMU-8941234 : Last ARI =  0.0542976793213463 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  30.9 % remaining..."
[1] "Last RXN_ID =  R-MMU-5672843 : Last ARI =  0.427200215800687 : Last ECOUNT =  6 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  30.7 % remaining..."
[1] "Last RXN_ID =  R-MMU-169895 : Last ARI =  0.131182599325191 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  30.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-140823 : Last ARI =  0.347465646424637 : Last ECOUNT =  3 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  30.5 % remaining..."
[1] "Last RXN

[1] "Last RXN_ID =  R-MMU-186550 : Last ARI =  0.0797090701065035 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  24.9 % remaining..."
[1] "Last RXN_ID =  R-MMU-2530501 : Last ARI =  0.0980379415443609 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  24.7 % remaining..."
[1] "Last RXN_ID =  R-MMU-3928605 : Last ARI =  0.0305301583231821 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  24.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-8854052 : Last ARI =  0.209719116858275 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  24.5 % remaining..."
[1] "Last RXN_ID =  R-MMU-6814091 : Last ARI =  0.246244075423587 : Last ECOUNT =  3 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  24.4 % remaining..."
[1] "Last RXN_ID =  R-MMU-9615031 : Last ARI =  0.0150131457740429 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  24.2 % remaining..."
[1] "La

[1] "Last RXN_ID =  R-MMU-1482548 : Last ARI =  0.0510736314863846 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  18.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-5621571 : Last ARI =  0.00805261734551602 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  18.5 % remaining..."
[1] "Last RXN_ID =  R-MMU-194308 : Last ARI =  0.0312922205666026 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  18.4 % remaining..."
[1] "Last RXN_ID =  R-MMU-5651789 : Last ARI =  -0.0130662662758843 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  18.2 % remaining..."
[1] "Last RXN_ID =  R-MMU-9724753 : Last ARI =  0.164135056387078 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  18.1 % remaining..."
[1] "Last RXN_ID =  R-MMU-428888 : Last ARI =  0.107535831749815 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  18 % remaining..."
[1] "Las

[1] "Last RXN_ID =  R-MMU-391934 : Last ARI =  0.0274488246967703 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  12.4 % remaining..."
[1] "Last RXN_ID =  R-MMU-9664850 : Last ARI =  0.0289935163466598 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  12.2 % remaining..."
[1] "Last RXN_ID =  R-MMU-8854209 : Last ARI =  0.0478821101474446 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  12.1 % remaining..."
[1] "Last RXN_ID =  R-MMU-1638032 : Last ARI =  0.0198555905545857 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  12 % remaining..."
[1] "Last RXN_ID =  R-MMU-1236955 : Last ARI =  0.0558546144200192 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  11.9 % remaining..."
[1] "Last RXN_ID =  R-MMU-196417 : Last ARI =  0.118438338550118 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  11.7 % remaining..."
[1] "Last

[1] "Last RXN_ID =  R-MMU-2559568 : Last ARI =  0.0913906145944556 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  6.1 % remaining..."
[1] "Last RXN_ID =  R-MMU-2870221 : Last ARI =  -0.00106966633361512 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  6 % remaining..."
[1] "Last RXN_ID =  R-MMU-4641206 : Last ARI =  0.05755323759614 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  5.9 % remaining..."
[1] "Last RXN_ID =  R-MMU-1855214 : Last ARI =  0.0555682225776487 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  5.7 % remaining..."
[1] "Last RXN_ID =  R-MMU-9709317 : Last ARI =  0.209325037161629 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  5.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-374663 : Last ARI =  0.0779106720674641 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  5.5 % remaining..."
[1] "Last RXN_

In [29]:
%%R
saveRDS(
   rxn_knn_misclass_rate.nls,
   paste(OUT_DIR, "toi_rxn_knn_misclass_rate_nls.Rds", sep = "")
)
saveRDS(rxn_knn_ari.nls,
        paste(OUT_DIR, "toi_rxn_knn_ari_nls.Rds", sep = ""))
saveRDS(rxn_knn_ecount.nls,
        paste(OUT_DIR, "toi_rxn_knn_ecount_nls.Rds", sep = ""))

In [30]:
%%R
d <- data.frame(
   RXN_ID = names(rxn2ensembls.nls),
   MISCLASS = unlist(rxn_knn_misclass_rate.nls),
   ARI = unlist(rxn_knn_ari.nls),
   ECOUNT = unlist(rxn_knn_ecount.nls)
)
print(d)
saveRDS(d, paste(OUT_DIR, "toi_summary_df.Rds", sep = ""))

                           RXN_ID    MISCLASS           ARI ECOUNT
R-MMU-450466.0.00    R-MMU-450466 0.000000000  8.522504e-01     17
R-MMU-450466.30.00   R-MMU-450551 0.000000000  3.396079e-01      4
R-MMU-450466.0.01    R-MMU-450580 0.031174089  3.396079e-01      4
R-MMU-450466.0.03     R-MMU-72103 0.023346829  8.144023e-01     22
R-MMU-450466.0.30   R-MMU-9770119 0.000000000  8.112229e-01     32
R-MMU-450466.1.00   R-MMU-9770141 0.000000000  8.794072e-01     60
R-MMU-450466.3.00   R-MMU-9770142 0.000000000  8.862550e-01     66
R-MMU-450466.0.10   R-MMU-9770145 0.000000000  8.784945e-01     74
R-MMU-450466.10.00  R-MMU-9770236 0.000000000  8.816168e-01     58
R-MMU-450551.0.00   R-MMU-6798748 0.000000000  8.955448e-01     55
R-MMU-450551.30.00  R-MMU-6800434 0.000000000  8.852956e-01     69
R-MMU-450551.0.01   R-MMU-6791218 0.107422402  7.552835e-01     30
R-MMU-450551.0.03   R-MMU-6791222 0.086099865  8.505089e-01     36
R-MMU-450551.0.30   R-MMU-1605595 0.000000000  5.565324e-01   

R-MMU-1605595.0.30  R-MMU-5655466 0.000000000  3.133787e-01      6
R-MMU-1605595.1.00  R-MMU-5655481 0.000000000  3.133787e-01      6
R-MMU-1605595.3.00  R-MMU-5655835 0.000000000  5.769740e-01      8
R-MMU-1605595.0.10  R-MMU-5655892 0.000000000  5.769740e-01      8
R-MMU-1605595.10.00 R-MMU-5655965 0.000000000  5.769740e-01      8
R-MMU-1605624.0.00  R-MMU-5656105 0.000000000  6.525207e-01      8
R-MMU-1605624.30.00 R-MMU-5656148 0.000000000  6.525207e-01      8
R-MMU-1605624.0.01  R-MMU-5656158 0.099527665  6.525207e-01      8
R-MMU-1605624.0.03  R-MMU-5684875 0.067881242  3.877966e-01      9
R-MMU-1605624.0.30  R-MMU-5684882 0.000000000  5.697431e-01     14
R-MMU-1605624.1.00  R-MMU-5684887 0.000000000  5.697431e-01     14
R-MMU-1605624.3.00  R-MMU-5685011 0.000000000  5.530769e-01     12
R-MMU-1605624.0.10  R-MMU-5685156 0.000000000  5.530769e-01     12
R-MMU-1605624.10.00 R-MMU-5686642 0.000000000  5.660706e-01     14
R-MMU-1605717.0.00  R-MMU-5686657 0.000000000  6.349329e-01   

R-MMU-71218.0.00     R-MMU-432164 0.000000000  2.560217e-01      8
R-MMU-71218.30.00    R-MMU-438037 0.000000000  5.160652e-01     13
R-MMU-71218.0.01     R-MMU-443767 0.117071525  1.569777e-01      3
R-MMU-71218.0.03     R-MMU-451283 0.107219973  3.651273e-01      7
R-MMU-71218.0.30     R-MMU-451311 0.000000000  3.651273e-01      7
R-MMU-71218.1.00    R-MMU-5672965 0.000000000  8.504898e-01     56
R-MMU-71218.3.00    R-MMU-6797554 0.000000000  2.896101e-01      7
R-MMU-71218.0.10    R-MMU-8849891 0.000000000  1.368039e-01      4
R-MMU-71218.10.00   R-MMU-9668214 0.000000000  7.387208e-02      1
R-MMU-8940388.0.00   R-MMU-209891 0.000000000  7.620869e-02      1
R-MMU-8940388.30.00 R-MMU-1454781 0.000000000  4.031846e-01      5
R-MMU-8940388.0.01  R-MMU-1564112 0.049662618  2.528189e-01      3
R-MMU-8940388.0.03  R-MMU-1592297 0.054655870  2.722250e-01      2
R-MMU-8940388.0.30  R-MMU-1602484 0.000000000  2.125334e-01      2
R-MMU-8940388.1.00  R-MMU-3215448 0.000000000  4.652681e-01   

R-MMU-4396387.1.00   R-MMU-141423 0.000000000  5.032630e-01     11
R-MMU-4396387.3.00   R-MMU-174057 0.000000000  4.254254e-01      9
R-MMU-4396387.0.10   R-MMU-174058 0.000000000  8.021486e-01     24
R-MMU-4396387.10.00  R-MMU-174070 0.000000000  4.254254e-01      9
R-MMU-5211235.0.00   R-MMU-174079 0.000000000  4.869005e-01     10
R-MMU-5211235.30.00  R-MMU-174088 0.000000000  4.981605e-01     11
R-MMU-5211235.0.01   R-MMU-174104 0.096356275  5.032630e-01     11
R-MMU-5211235.0.03   R-MMU-174105 0.072941970  8.193685e-01     27
R-MMU-5211235.0.30   R-MMU-174119 0.000000000  4.713639e-01     10
R-MMU-5211235.1.00   R-MMU-174120 0.000000000  4.254254e-01      9
R-MMU-5211235.3.00   R-MMU-174121 0.000000000  4.254254e-01      9
R-MMU-5211235.0.10   R-MMU-174132 0.000000000  4.254254e-01      9
R-MMU-5211235.10.00  R-MMU-174139 0.000000000  4.254254e-01      9
R-MMU-5250930.0.00   R-MMU-174144 0.000000000  4.254254e-01      9
R-MMU-5250930.30.00  R-MMU-174157 0.000000000  4.254254e-01   

R-MMU-9620515.30.00 R-MMU-8852280 0.000000000  4.899553e-01      5
R-MMU-9620515.0.01  R-MMU-8852298 0.096693657  4.899553e-01      5
R-MMU-9620515.0.03  R-MMU-8852306 0.099190283  4.899553e-01      5
R-MMU-9620515.0.30  R-MMU-8865774 0.000000000  5.204928e-01      7
R-MMU-9620515.1.00  R-MMU-8867370 0.000000000  5.741310e-01      7
R-MMU-9620515.3.00  R-MMU-9610428 0.000000000  5.512631e-01      8
R-MMU-9620515.0.10  R-MMU-9610641 0.000000000  5.512631e-01      8
R-MMU-9620515.10.00 R-MMU-9646393 0.000000000  5.114916e-01      6
R-MMU-9677051.0.00  R-MMU-9646679 0.000000000  8.188326e-01     17
R-MMU-9677051.30.00 R-MMU-9646685 0.000000000  8.188326e-01     17
R-MMU-9677051.0.01  R-MMU-9648017 0.094197031  4.899553e-01      5
R-MMU-9677051.0.03  R-MMU-9648114 0.091363023  8.828644e-01     58
R-MMU-9677051.0.30  R-MMU-9668419 0.000000000  6.361803e-01     11
R-MMU-9677051.1.00   R-MMU-983259 0.000000000  7.586826e-01     23
R-MMU-9677051.3.00   R-MMU-983266 0.000000000  7.586826e-01   

...

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



 0.000000000  8.343671e-01     20
R-MMU-5689544.0.10  R-MMU-8956140 0.000000000  8.303865e-01     18
R-MMU-5689544.10.00 R-MMU-8956184 0.000000000  8.303865e-01     18
R-NUL-2179307.0.00  R-MMU-8957265 0.000000000  8.433691e-01     22
R-NUL-2179307.30.00 R-MMU-9755303 0.000000000  8.905304e-01     28
R-NUL-2179307.0.01  R-MMU-9755306 0.114979757  8.493521e-01     21
R-NUL-2179307.0.03  R-MMU-9762096 0.093994602  8.588902e-01     22
R-NUL-2179307.0.30   R-MMU-983150 0.000000000  8.493521e-01     21
R-NUL-2179307.1.00  R-MMU-4720446 0.000000000  1.992792e-01      3
R-NUL-2179307.3.00  R-MMU-8854628 0.000000000  7.598024e-01      8
R-NUL-2179307.0.10  R-MMU-9024326 0.000000000  5.171722e-01      6
R-NUL-2179307.10.00 R-MMU-9024334 0.000000000  5.171722e-01      6
R-NUL-2179313.0.00  R-MMU-9029517 0.000000000  3.753811e-01      4
R-NUL-2179313.30.00 R-MMU-9029551 0.000000000  3.395619e-01      4
R-NUL-2179313.0.01  R-MMU-9029561 0.114979757  3.395619e-01      4
R-NUL-2179313.0.03  R-MMU-90

R-MMU-482767.0.01   R-MMU-9670101 0.102091768  4.762361e-01     36
R-MMU-482767.0.03   R-MMU-9670114 0.114709852  5.143541e-01     37
R-MMU-482767.0.30   R-MMU-3000112 0.000000000  4.950715e-02      1
R-MMU-482767.1.00   R-MMU-3000122 0.000000000  4.950715e-02      1
R-MMU-482767.3.00    R-MMU-912355 0.000000000  6.379986e-01     55
R-MMU-482767.0.10    R-MMU-912362 0.000000000  1.576601e-01      4
R-MMU-482767.10.00   R-MMU-912423 0.000000000  4.863579e-01     37
R-MMU-5665751.0.00   R-MMU-912449 0.000000000  4.863579e-01     37
R-MMU-5665751.30.00  R-MMU-912468 0.000000000  4.863579e-01     37
R-MMU-5665751.0.01   R-MMU-912506 0.070377868  2.859108e-01      8
R-MMU-5665751.0.03   R-MMU-909725 0.033738192  2.489059e-01      2
R-MMU-5665751.0.30  R-MMU-9710959 0.000000000  2.489059e-01      2
R-MMU-5665751.1.00   R-MMU-514604 0.000000000  1.154618e-02      1
R-MMU-5665751.3.00  R-MMU-9837333 0.000000000  1.273696e-01      1
R-MMU-5665751.0.10   R-MMU-163217 0.000000000  7.509263e-01   

R-MMU-482788.0.10   R-MMU-5632654 0.000000000  1.573889e-01      2
R-MMU-482788.10.00  R-MMU-9759844 0.000000000  1.008462e-01      2
R-MMU-5632738.0.00  R-MMU-9815762 0.000000000  9.652965e-02      1
R-MMU-5632738.30.00 R-NUL-5362792 0.000000000  9.822927e-02      1
R-MMU-5632738.0.01   R-MMU-109638 0.049595142  7.021416e-01     15
R-MMU-5632738.0.03   R-MMU-112381 0.057422402  7.098138e-01     16
R-MMU-5632738.0.30   R-MMU-113402 0.000000000  5.643539e-01     11
R-MMU-5632738.1.00   R-MMU-113407 0.000000000  5.325874e-01     10
R-MMU-5632738.3.00   R-MMU-113409 0.000000000  5.643539e-01     11
R-MMU-5632738.0.10    R-MMU-72095 0.000000000  5.376378e-01      9
R-MMU-5632738.10.00   R-MMU-73946 0.000000000  7.403748e-01     23
R-MMU-5672824.0.00    R-MMU-75095 0.000000000  6.841291e-01     18
R-MMU-5672824.30.00   R-MMU-75850 0.000000000  7.403748e-01     23
R-MMU-5672824.0.01    R-MMU-75856 0.088663968  7.403748e-01     23
R-MMU-5672824.0.03    R-MMU-75861 0.059986505  7.403748e-01   

R-MMU-8950453.0.03    R-MMU-68919 0.112010796  2.619440e-01      8
R-MMU-8950453.0.30    R-MMU-68940 0.000000000  2.619440e-01      8
R-MMU-8950453.1.00    R-MMU-68944 0.000000000  3.477937e-01      9
R-MMU-8950453.3.00    R-MMU-69019 0.000000000  1.146326e-01      2
R-MMU-8950453.0.10  R-MMU-9749253 0.000000000  1.146326e-01      2
R-MMU-8950453.10.00 R-MMU-9757258 0.000000000  1.146326e-01      2
R-MMU-8983519.0.00   R-MMU-444773 0.000000000  1.275537e-01      1
R-MMU-8983519.30.00  R-MMU-879674 0.000000000  1.275537e-01      1
R-MMU-8983519.0.01  R-MMU-2426496 0.115114710  3.681755e-01      4
R-MMU-8983519.0.03  R-MMU-2426528 0.112010796  3.681755e-01      4
R-MMU-8983519.0.30  R-MMU-2426626 0.000000000  2.643112e-01      3
R-MMU-8983519.1.00  R-MMU-2447193 0.000000000  2.643112e-01      3
R-MMU-8983519.3.00  R-MMU-2447196 0.000000000  3.187544e-01      3
R-MMU-8983519.0.10  R-MMU-2465886 0.000000000  1.172693e-01      1
R-MMU-8983519.10.00 R-MMU-2533953 0.000000000  2.782634e-01   

In [31]:
%%R
library(htmlwidgets)
min_misclass_pca <-
   prcomp(t(vst.count.mtx.train[rxn2ensembls.nls[["R-MMU-450466"]], ]), scale. = T)
pca.d <- data.frame(
   PC1 = min_misclass_pca$x[, 1],
   PC2 = min_misclass_pca$x[, 2],
   PC3 = min_misclass_pca$x[, 3],
   Section = tcdd_dose_detail.vec.train
)
ggplot(pca.d) +
   geom_point(aes(x = PC1, y = PC2, colour = Section)) +
   theme_bw()
p <- plot_ly(
   x = pca.d$PC1,
   y = pca.d$PC2,
   z = pca.d$PC3,
   type = "scatter3d",
   mode = "markers",
   color = pca.d$Section,
   size = 1
)
saveWidget(p, "plotly_chart.html", selfcontained = TRUE)